In [1]:
import requests
import os
import pandas as pd
import numpy as np
pd.set_option('display.max_columns', None)
import warnings 
warnings.filterwarnings('ignore')

#### Dependent Variables
    For every matches  played ,the results can be Win , Draw or Loss and they are mutually exclusive

#### Table Like metrics
    This is similar to the data from the log containing the cummulative sum i.e league table
    
##### Average Like metrics
    This is similar to the data from the log containing the cummulative avg i.e league table
    
#### Venue like metric
    Some teams play better  at home than on the road ,vice versa
        
        * i.e Liverpool rarely lose at the Anfield and Manchester city at the Etihad stadium
        * Also United had a long streak of unbeaten on the road
     So we pick out Away win , Away Loss , Away Draw  , Home win , home draw and Home loss

#### rolling metrics
    We can input data like goal scored, possesion into our features because of data leakage.
    So we take rolling averages for the a specific window i.e sums or averages from the last two games,three games e.t.c
    
#### last games metric
    We look at result from previous match played.
    i.e the last opponent, previous competition , number of resting days
    
#### Played_Opp_X_times
    Maybe this doesnt count in football games .But in the basketball games where each team have the sets they run and plays
    they call.Number of times youve played an opponent is a factor when we consider familiarity
    
####  monthly metrics
    Football is a steaky sport and here we calculate GF,GA,Wins and other target variable for that month
    
#### Prev Month
    As mentioned earlier team confidence plays a key part in winning football games 
    
#### Trim Captain
    Some teams ,the captain is the enforcer e.g Zlatan, Sergio Ramos and some are cool headed i.e Leo Messi, Eden Hazard.
    Captains are the Coach within the four lines of the pitch and they infuence the decisions of their teammates.
    So we trim the captain feature to is it the Captain or Vice Captain or other player.
    
#### get_cum_by_col
    Here we get cummulative sum or average for columns like Win,Lose,Draw,GF,GA,Poss
    * Groupby  Venue
    * Groupby  Formation
    * Groupby  Opponent


In [210]:
def All_Transformation(df):
    df = df.copy()
    df['Month'] = df.Date.dt.month
    df.loc[:,'GA'] = df.GA.apply(to_int)
    df.loc[:,'GF'] = df.GF.apply(to_int)
    
    df['Win'] = df.apply(lambda x : 1 if x.Result == 'W' else 0 ,axis=1)
    df['Draw'] = df.apply(lambda x : 1 if x.Result == 'D' else 0 ,axis=1)
    df['Lose'] = df.apply(lambda x : 1 if x.Result == 'L' else 0 ,axis=1)
    
    #Table Like metrics
    df['Points'] = df.apply(lambda x : 3 if x.Result == 'W' else (1 if x.Result == 'D' else 0) ,axis=1)
    df['Total_Points'] = df.Points.shift(1).cumsum()
    df['Total_GF'] = df.GF.shift(1).cumsum()
    df['Total_GA'] = df.GA.shift(1).cumsum()
    df['Total_Win'] = df.Win.shift(1).cumsum()
    df['Total_Draw'] = df.Draw.shift(1).cumsum()
    df['Total_Loss'] = df.Lose.shift(1).cumsum()
    
    #Average Like metrics
    df['Points_Avg_for_szn'] = df.Points.shift(1).expanding().mean()
    df['GF_Avg_for_szn'] = df.GF.shift(1).expanding().mean()
    df['GA_Avg_for_szn'] = df.GA.shift(1).expanding().mean()
    df['Win_Avg_for_szn'] = df.Win.shift(1).expanding().mean()
    df['Draw_Avg_for_szn'] = df.Draw.shift(1).expanding().mean()
    df['Loss_Avg_for_szn'] = df.Lose.shift(1).expanding().mean()
    
    #Venue like metric
    df['Away_Win'] = df.apply(lambda x : 1 if x.Venue == 'Away' and x.Result == 'W' else 0 ,axis=1)
    df['Away_Draw'] = df.apply(lambda x : 1 if x.Venue == 'Away' and x.Result == 'D' else 0 ,axis=1)
    df['Away_Loss'] = df.apply(lambda x : 1 if x.Venue == 'Away' and x.Result == 'L' else 0 ,axis=1)
    df['Home_Win'] = df.apply(lambda x : 1 if x.Venue == 'Home' and x.Result == 'W' else 0 ,axis=1)
    df['Home_Draw'] = df.apply(lambda x : 1 if x.Venue == 'Home' and x.Result == 'D' else 0 ,axis=1)
    df['Home_Loss'] = df.apply(lambda x : 1 if x.Venue == 'Home' and x.Result == 'L' else 0 ,axis=1)
    
    #rolling metrics
    df = rolling_average_or_sum(df,
                                cols=['Points','Win','Draw','Lose','GF','GA',
                                      'Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'],
                                window=1,agg_func='sum')
    df = rolling_average_or_sum(df,cols=['Points','Win','Draw','Lose','GF','GA',
                                         'Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'],
                                window=2,agg_func='sum')
    df = rolling_average_or_sum(df,cols=['Points','Win','Draw','Lose','GF','GA',
                                         'Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss','Poss'],
                                window=3,agg_func='mean')
    #last games metric
    df['Prev_match_date'] = df.Date.shift(1)
    df['Rest'] = df.Date - df.Prev_match_date
    df['Prev_comp'] = df.Comp.shift(1)
    df['Prev_Opp'] = df.Opponent.shift(1)
    
    df.loc[:,'Played_Opp_X_times'] = df.apply( get_no_of_time_opp_faced,axis='columns')
    
    month_cols = cols = ['GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss']
    
    #monthly metrics   
    df = previous_month_agg(df,month_cols,'sum')
    df = previous_month_agg(df=df,cols=['GF','GA'],agg_func='mean')
    
    # prev month metrics
    df = previous_month_agg(df=df,cols=['Poss'],agg_func='mean')
    
    df = Trim_Captain(df)
    
    df = get_cum_by_col(df,grouper='Venue',grouper_name='Venue',cols=['Poss','GF','GA'],agg_func='mean')
    df = get_cum_by_col(df,grouper='Venue',grouper_name='Venue',cols=['Win','Lose','Draw','GF','GA'],agg_func='sum')
    df = get_cum_by_col(df,grouper='Formation',grouper_name='Formation',cols=['Poss','GF','GA'],agg_func='mean')
    df = get_cum_by_col(df,grouper='Formation',grouper_name='Formation',cols=['Win','Lose','Draw','GF','GA'],agg_func='sum')
    df = get_cum_by_col(df,grouper='Opponent',grouper_name='Opp',cols=['Poss','GA','GF'],agg_func='mean')
    df = get_cum_by_col(df,grouper='Opponent',grouper_name='Opp',cols=['Win','Lose','Draw','GA','GF'],agg_func='sum')
    print(df.shape)
    return df

In [194]:
df = pd.read_csv("C:\\Users\\user\\Solo Dolo\\EPL Analysis\\2018_2022_data/2018Liverpool.csv",parse_dates=['Date'])

In [211]:
All_Transformation(df)

(56, 249)


Unnamed: 0       Date   Time            Comp           Round  Day  \
0            0 2017-08-12  12:30  Premier League     Matchweek 1  Sat   
1            1 2017-08-15  20:45    Champions Lg  Play-off round  Tue   
2            2 2017-08-19  15:00  Premier League     Matchweek 2  Sat   
3            3 2017-08-23  19:45    Champions Lg  Play-off round  Wed   
4            4 2017-08-27  16:00  Premier League     Matchweek 3  Sun   
5            5 2017-09-09  12:30  Premier League     Matchweek 4  Sat   
6            6 2017-09-13  19:45    Champions Lg     Group stage  Wed   
7            7 2017-09-16  15:00  Premier League     Matchweek 5  Sat   
8            8 2017-09-19  19:45         EFL Cup     Third round  Tue   
9            9 2017-09-23  17:30  Premier League     Matchweek 6  Sat   
10          10 2017-09-26  21:45    Champions Lg     Group stage  Tue   
11          11 2017-10-01  16:30  Premier League     Matchweek 7  Sun   
12          12 2017-10-14  12:30  Premier League     Matchweek 8  Sat   
13          13 2017-10-17  20:45    Champions Lg     Group stage  Tue   
14          14 2017-10-22  16:00  Premier League     Matchweek 9  Sun   
15          15 2017-10-28  15:00  Premier League    Matchweek 10  Sat   
16          16 2017-11-01  19:45    Champions Lg     Group stage  Wed   
17          17 2017-11-04  17:30  Premier League    Matchweek 11  Sat   
18          18 2017-11-18  15:00  Premier League    Matchweek 12  Sat   
19          19 2017-11-21  20:45    Champions Lg     Group stage  Tue   
20          20 2017-11-25  17:30  Premier League    Matchweek 13  Sat   
21          21 2017-11-29  20:00  Premier League    Matchweek 14  Wed   
22          22 2017-12-02  15:00  Premier League    Matchweek 15  Sat   
23          23 2017-12-06  19:45    Champions Lg     Group stage  Wed   
24          24 2017-12-10  14:15  Premier League    Matchweek 16  Sun   
25          25 2017-12-13  20:00  Premier League    Matchweek 17  Wed   
26          26 2017-12-17  16:30  Premier League    Matchweek 18  Sun   
27          27 2017-12-22  19:45  Premier League    Matchweek 19  Fri   
28          28 2017-12-26  17:30  Premier League    Matchweek 20  Tue   
29          29 2017-12-30  15:00  Premier League    Matchweek 21  Sat   
30          30 2018-01-01  15:00  Premier League    Matchweek 22  Mon   
31          31 2018-01-05  19:55          FA Cup     Third round  Fri   
32          32 2018-01-14  16:00  Premier League    Matchweek 23  Sun   
33          33 2018-01-22  20:00  Premier League    Matchweek 24  Mon   
34          34 2018-01-27  19:45          FA Cup    Fourth round  Sat   
35          35 2018-01-30  20:00  Premier League    Matchweek 25  Tue   
36          36 2018-02-04  16:30  Premier League    Matchweek 26  Sun   
37          37 2018-02-11  16:30  Premier League    Matchweek 27  Sun   
38          38 2018-02-14  19:45    Champions Lg     Round of 16  Wed   
39          39 2018-02-24  15:00  Premier League    Matchweek 28  Sat   
40          40 2018-03-03  17:30  Premier League    Matchweek 29  Sat   
41          41 2018-03-06  19:45    Champions Lg     Round of 16  Tue   
42          42 2018-03-10  12:30  Premier League    Matchweek 30  Sat   
43          43 2018-03-17  17:30  Premier League    Matchweek 31  Sat   
44          44 2018-03-31  12:30  Premier League    Matchweek 32  Sat   
45          45 2018-04-04  19:45    Champions Lg  Quarter-finals  Wed   
46          46 2018-04-07  12:30  Premier League    Matchweek 33  Sat   
47          47 2018-04-10  19:45    Champions Lg  Quarter-finals  Tue   
48          48 2018-04-14  17:30  Premier League    Matchweek 34  Sat   
49          49 2018-04-21  12:30  Premier League    Matchweek 35  Sat   
50          50 2018-04-24  19:45    Champions Lg     Semi-finals  Tue   
51          51 2018-04-28  12:30  Premier League    Matchweek 36  Sat   
52          52 2018-05-02  20:45    Champions Lg     Semi-finals  Wed   
53          53 2018-05-06  16:30  Premier League    Matchweek 

In [204]:
df['Captain']

0      Jordan Henderson
1      Jordan Henderson
2      Jordan Henderson
3      Jordan Henderson
4      Jordan Henderson
5      Jordan Henderson
6      Jordan Henderson
7          James Milner
8      Jordan Henderson
9      Jordan Henderson
10     Jordan Henderson
11     Jordan Henderson
12     Jordan Henderson
13         James Milner
14     Jordan Henderson
15     Jordan Henderson
16         James Milner
17       Simon Mignolet
18     Jordan Henderson
19     Jordan Henderson
20     Jordan Henderson
21       Simon Mignolet
22     Jordan Henderson
23    Philippe Coutinho
24     Jordan Henderson
25    Philippe Coutinho
26     Jordan Henderson
27     Jordan Henderson
28    Philippe Coutinho
29         James Milner
30       Simon Mignolet
31         James Milner
32         Dejan Lovren
33             Emre Can
34       Alberto Moreno
35     Jordan Henderson
36     Jordan Henderson
37             Emre Can
38     Jordan Henderson
39         James Milner
40     Jordan Henderson
41     Jordan He

In [66]:
df['Month'] = df.Date.dt.month

In [67]:
df['Month'].value_counts()

12    8
4     7
9     6
11    6
1     6
8     5
10    5
3     5
2     4
5     4
Name: Month, dtype: int64

In [68]:
df.Month.unique()

array([ 8,  9, 10, 11, 12,  1,  2,  3,  4,  5], dtype=int64)

## Month
* The season started in August 
* Treat as cyclic data

In [17]:
def to_int(row):
    if isinstance(row,int) or isinstance(row,float):
        return row 
    tokens = row.split(' ')
    if len(tokens) ==2:
        return int(tokens[0])
    try:
        return int(row)
    except ValueError:
        return np.nan#int(row.GF.split(' ')[0])

In [17]:
def to_int(row):
    if row.isdigit():
         return int(row)
    else:
        tokens = row.split(' ')
        if len(tokens) ==2:
            return int(tokens[0])

In [7]:
df.xG.dtype# == 'int64'

dtype('float64')

In [22]:
df.GF.str.split(' ')[0]

['1', '(6)']

In [69]:
df.loc[:,'GA'] = df.GA.apply(to_int)

In [70]:
df.loc[:,'GF'] = df.GF.apply(to_int)

In [71]:
df.GF

0     3
1     2
2     1
3     4
4     4
5     0
6     2
7     1
8     0
9     3
10    1
11    1
12    0
13    7
14    1
15    3
16    3
17    4
18    3
19    3
20    1
21    3
22    5
23    7
24    1
25    0
26    4
27    3
28    5
29    2
30    2
31    2
32    4
33    0
34    2
35    3
36    2
37    2
38    5
39    4
40    2
41    0
42    1
43    5
44    2
45    3
46    0
47    2
48    3
49    2
50    5
51    0
52    2
53    0
54    4
55    1
Name: GF, dtype: int64

In [72]:
df['Prev_match_date'] = df.Date.shift(1)

In [73]:
df['Rest'] = df.Date - df.Prev_match_date
df['Prev_comp'] = df.Comp.shift(1)

In [142]:
df['Prev_Opp'] = df.Opponent.shift(1)

In [74]:
df[df.Comp == 'Premier League']['Referee'].value_counts()

Kevin Friend       5
Anthony Taylor     4
Craig Pawson       4
Martin Atkinson    4
Andre Marriner     4
Niel Swarbrick     4
Jonathan Moss      2
Roger East         2
Michael Oliver     2
Graham Scott       2
Stuart Attwell     2
Mike Jones         1
Paul Tierney       1
Chris Kavanagh     1
Name: Referee, dtype: int64

## Referee
* Lets look at Michael Oliver and Anthony ...Chelsea villian lol

In [75]:
ant_and_oli = df[(df.Referee == 'Anthony Taylor') |  (df.Referee == 'Michael Oliver')]
ant_and_oli[['Referee','Opponent','Venue','GF','GA','Result']]

Referee        Opponent Venue  GF  GA Result
0   Anthony Taylor         Watford  Away   3   3      D
9   Anthony Taylor  Leicester City  Away   3   2      W
20  Michael Oliver         Chelsea  Home   1   1      D
43  Anthony Taylor         Watford  Home   5   0      W
46  Michael Oliver         Everton  Away   0   0      D
53  Anthony Taylor         Chelsea  Away   0   1      L

In [76]:
df.Formation.value_counts()

4-3-3      46
4-2-3-1     5
4-4-2       3
3-5-1-1     1
4-4-1-1     1
Name: Formation, dtype: int64

In [77]:
pd.DataFrame(df.groupby(['Formation','Result'])['Result'].agg('count'))

Result
Formation Result        
3-5-1-1   W            1
4-2-3-1   D            1
          L            1
          W            3
4-3-3     D           14
          L            8
          W           24
4-4-1-1   W            1
4-4-2     D            1
          W            2

## Formation
* Earlier in the season Chelsea played 3 men defense
* Then 4-2-2 was adopted

In [78]:
pd.DataFrame(df.groupby(['Day','Result'])['Result'].agg('count'))

Result
Day Result        
Fri D            1
    W            1
Mon L            1
    W            1
Sat D            7
    L            4
    W           12
Sun D            3
    L            2
    W            5
Tue D            3
    L            1
    W            6
Wed D            2
    L            1
    W            6

In [79]:
pd.DataFrame(df.groupby(['Rest','Result'])['Result'].agg('count'))

Result
Rest    Result        
2 days  W            1
3 days  D            6
        L            1
        W            8
4 days  D            4
        L            3
        W           13
5 days  D            3
        L            2
6 days  W            1
7 days  D            1
        W            4
8 days  L            1
9 days  W            1
10 days W            1
13 days D            1
        L            2
14 days W            2

In [40]:
#Opp_faced = df.Opponent.value_counts().to_dict()
#df['N'] = df['BsmtFinType1'].map(bsmf_map).astype('int')
def get_no_of_time_opp_faced(row):
    present_date = row.Prev_match_date
    if present_date is np.nan:
        pass
    back_df = df[df.Date<=present_date]
    Opp_faced = back_df.Opponent.value_counts().to_dict()
    if row.Opponent not  in Opp_faced.keys():
        return 0
    #display(Opp_faced)
    return Opp_faced[row.Opponent]

In [80]:
df.loc[:,'OPPPP'] = df.apply( get_no_of_time_opp_faced,axis='columns')

In [81]:
df[['OPPPP','Opponent']].head()

OPPPP        Opponent
0      0         Watford
1      0   de Hoffenheim
2      0  Crystal Palace
3      1   de Hoffenheim
4      0         Arsenal

In [82]:
pd.DataFrame(df.groupby(['OPPPP','Result'])['Result'].agg('count'))

Result
OPPPP Result        
0     D            9
      L            4
      W           14
1     D            5
      L            5
      W           16
2     D            2
      W            1

In [144]:
#Table Like metrics
df['Points'] = df.apply(lambda x : 3 if x.Result == 'W' else (1 if x.Result == 'D' else 0) ,axis=1)
df['Total_Points'] = df.Points.shift(1).cumsum()
df['Total_GF'] = df.GF.shift(1).cumsum()
df['Total_GA'] = df.GA.shift(1).cumsum()
df['Total_Win'] = df.Win.shift(1).cumsum()
df['Total_Draw'] = df.Draw.shift(1).cumsum()
df['Total_Loss'] = df.Lose.shift(1).cumsum()

In [147]:
#Average Like metrics
df['Points_Avg_for_szn'] = df.Points.shift(1).expanding().mean()
df['GF_Avg_for_szn'] = df.GF.shift(1).expanding().mean()
df['GA_Avg_for_szn'] = df.GA.shift(1).expanding().mean()
df['Win_Avg_for_szn'] = df.Win.shift(1).expanding().mean()
df['Draw_Avg_for_szn'] = df.Draw.shift(1).expanding().mean()
df['Loss_Avg_for_szn'] = df.Lose.shift(1).expanding().mean()

In [169]:
def rolling_average_or_sum(df,cols,window,agg_func):
    df = df.copy()
    alias = '_last_'+str(window)+'gm_'+agg_func
    new_cols = [col+alias for col in cols]
    if agg_func == 'sum':
        rolling = df[cols].shift(1).rolling(window).sum()
    if agg_func == 'mean':
        rolling = df[cols].shift(1).rolling(window).mean()
    rolling.columns = new_cols
    df_rolling = pd.concat([df,rolling],axis=1)
    return df_rolling

In [186]:
corr_cols = ['Day', 'Venue', 'Result','GF', 'GA','Win','Lose','Draw','Poss','Away_Win','Month',
 'Away_Draw',
 'Away_Loss',
 'Home_Win',
 'Home_Draw',
 'Home_Loss',
 'Points',
 'Total_Points',
 'Prev_Opp',
 'Total_GF',
 'Total_GA',
 'Total_Win',
 'Total_Draw',
 'Total_Loss', 'Points_Avg_for_szn',
 'GF_Avg_for_szn',
 'GA_Avg_for_szn',
 'Win_Avg_for_szn',
 'Draw_Avg_for_szn',
 'Loss_Avg_for_szn',]

In [187]:

corre = df[corr_cols].corr()#['Win','Lose','Draw']

In [178]:
df.columns.to_list()

['Unnamed: 0',
 'Date',
 'Time',
 'Comp',
 'Round',
 'Day',
 'Venue',
 'Result',
 'GF',
 'GA',
 'Opponent',
 'xG',
 'xGA',
 'Poss',
 'Attendance',
 'Captain',
 'Formation',
 'Referee',
 'Match Report',
 'Notes',
 'Team',
 'Standard_Gls',
 'Standard_Sh',
 'Standard_SoT',
 'Standard_SoT%',
 'Standard_G/Sh',
 'Standard_G/SoT',
 'Standard_Dist',
 'Standard_FK',
 'Standard_PK',
 'Standard_PKatt',
 'Expected_xG',
 'Expected_npxG',
 'Expected_npxG/Sh',
 'Expected_G-xG',
 'Expected_np:G-xG',
 'SCA_Types_SCA',
 'SCA_Types_PassLive',
 'SCA_Types_PassDead',
 'SCA_Types_Drib',
 'SCA_Types_Sh',
 'SCA_Types_Fld',
 'SCA_Types_Def',
 'GCA_Types_GCA',
 'GCA_Types_PassLive',
 'GCA_Types_PassDead',
 'GCA_Types_Drib',
 'GCA_Types_Sh',
 'GCA_Types_Fld',
 'GCA_Types_Def',
 'Tackles_Tkl',
 'Tackles_TklW',
 'Tackles_Def_3rd',
 'Tackles_Mid_3rd',
 'Tackles_Att_3rd',
 'Vs_Dribbles_Tkl',
 'Vs_Dribbles_Att',
 'Vs_Dribbles_Tkl%',
 'Vs_Dribbles_Past',
 'Pressures_Press',
 'Pressures_Succ',
 'Pressures_%',
 'Pressur

In [188]:
corre['Win']

GF                    0.686775
GA                   -0.483212
Win                   1.000000
Lose                 -0.487285
Draw                 -0.704273
Poss                 -0.049928
Away_Win              0.493772
Month                -0.064952
Away_Draw            -0.420883
Away_Loss            -0.420883
Home_Win              0.618064
Home_Draw            -0.487285
Home_Loss            -0.150151
Points                0.964608
Total_Points         -0.034028
Total_GF             -0.021355
Total_GA             -0.016786
Total_Win            -0.043844
Total_Draw            0.027445
Total_Loss           -0.002927
Points_Avg_for_szn   -0.143425
GF_Avg_for_szn        0.018219
GA_Avg_for_szn        0.025306
Win_Avg_for_szn      -0.178948
Draw_Avg_for_szn      0.225713
Loss_Avg_for_szn     -0.111769
Name: Win, dtype: float64

In [170]:
rolling_average_or_sum(df,cols=['Points','Win','Draw','Lose','GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'],window=1,agg_func='sum')

Unnamed: 0       Date   Time            Comp           Round  Day  \
0            0 2017-08-12  12:30  Premier League     Matchweek 1  Sat   
1            1 2017-08-15  20:45    Champions Lg  Play-off round  Tue   
2            2 2017-08-19  15:00  Premier League     Matchweek 2  Sat   
3            3 2017-08-23  19:45    Champions Lg  Play-off round  Wed   
4            4 2017-08-27  16:00  Premier League     Matchweek 3  Sun   
5            5 2017-09-09  12:30  Premier League     Matchweek 4  Sat   
6            6 2017-09-13  19:45    Champions Lg     Group stage  Wed   
7            7 2017-09-16  15:00  Premier League     Matchweek 5  Sat   
8            8 2017-09-19  19:45         EFL Cup     Third round  Tue   
9            9 2017-09-23  17:30  Premier League     Matchweek 6  Sat   
10          10 2017-09-26  21:45    Champions Lg     Group stage  Tue   
11          11 2017-10-01  16:30  Premier League     Matchweek 7  Sun   
12          12 2017-10-14  12:30  Premier League     Matchweek 8  Sat   
13          13 2017-10-17  20:45    Champions Lg     Group stage  Tue   
14          14 2017-10-22  16:00  Premier League     Matchweek 9  Sun   
15          15 2017-10-28  15:00  Premier League    Matchweek 10  Sat   
16          16 2017-11-01  19:45    Champions Lg     Group stage  Wed   
17          17 2017-11-04  17:30  Premier League    Matchweek 11  Sat   
18          18 2017-11-18  15:00  Premier League    Matchweek 12  Sat   
19          19 2017-11-21  20:45    Champions Lg     Group stage  Tue   
20          20 2017-11-25  17:30  Premier League    Matchweek 13  Sat   
21          21 2017-11-29  20:00  Premier League    Matchweek 14  Wed   
22          22 2017-12-02  15:00  Premier League    Matchweek 15  Sat   
23          23 2017-12-06  19:45    Champions Lg     Group stage  Wed   
24          24 2017-12-10  14:15  Premier League    Matchweek 16  Sun   
25          25 2017-12-13  20:00  Premier League    Matchweek 17  Wed   
26          26 2017-12-17  16:30  Premier League    Matchweek 18  Sun   
27          27 2017-12-22  19:45  Premier League    Matchweek 19  Fri   
28          28 2017-12-26  17:30  Premier League    Matchweek 20  Tue   
29          29 2017-12-30  15:00  Premier League    Matchweek 21  Sat   
30          30 2018-01-01  15:00  Premier League    Matchweek 22  Mon   
31          31 2018-01-05  19:55          FA Cup     Third round  Fri   
32          32 2018-01-14  16:00  Premier League    Matchweek 23  Sun   
33          33 2018-01-22  20:00  Premier League    Matchweek 24  Mon   
34          34 2018-01-27  19:45          FA Cup    Fourth round  Sat   
35          35 2018-01-30  20:00  Premier League    Matchweek 25  Tue   
36          36 2018-02-04  16:30  Premier League    Matchweek 26  Sun   
37          37 2018-02-11  16:30  Premier League    Matchweek 27  Sun   
38          38 2018-02-14  19:45    Champions Lg     Round of 16  Wed   
39          39 2018-02-24  15:00  Premier League    Matchweek 28  Sat   
40          40 2018-03-03  17:30  Premier League    Matchweek 29  Sat   
41          41 2018-03-06  19:45    Champions Lg     Round of 16  Tue   
42          42 2018-03-10  12:30  Premier League    Matchweek 30  Sat   
43          43 2018-03-17  17:30  Premier League    Matchweek 31  Sat   
44          44 2018-03-31  12:30  Premier League    Matchweek 32  Sat   
45          45 2018-04-04  19:45    Champions Lg  Quarter-finals  Wed   
46          46 2018-04-07  12:30  Premier League    Matchweek 33  Sat   
47          47 2018-04-10  19:45    Champions Lg  Quarter-finals  Tue   
48          48 2018-04-14  17:30  Premier League    Matchweek 34  Sat   
49          49 2018-04-21  12:30  Premier League    Matchweek 35  Sat   
50          50 2018-04-24  19:45    Champions Lg     Semi-finals  Tue   
51          51 2018-04-28  12:30  Premier League    Matchweek 36  Sat   
52          52 2018-05-02  20:45    Champions Lg     Semi-finals  Wed   
53          53 2018-05-06  16:30  Premier League    Matchweek 

In [189]:
rolling_average_or_sum(df,cols=['Points','Win','Draw','Lose','GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'],window=2,agg_func='sum')

Unnamed: 0       Date   Time            Comp           Round  Day  \
0            0 2017-08-12  12:30  Premier League     Matchweek 1  Sat   
1            1 2017-08-15  20:45    Champions Lg  Play-off round  Tue   
2            2 2017-08-19  15:00  Premier League     Matchweek 2  Sat   
3            3 2017-08-23  19:45    Champions Lg  Play-off round  Wed   
4            4 2017-08-27  16:00  Premier League     Matchweek 3  Sun   
5            5 2017-09-09  12:30  Premier League     Matchweek 4  Sat   
6            6 2017-09-13  19:45    Champions Lg     Group stage  Wed   
7            7 2017-09-16  15:00  Premier League     Matchweek 5  Sat   
8            8 2017-09-19  19:45         EFL Cup     Third round  Tue   
9            9 2017-09-23  17:30  Premier League     Matchweek 6  Sat   
10          10 2017-09-26  21:45    Champions Lg     Group stage  Tue   
11          11 2017-10-01  16:30  Premier League     Matchweek 7  Sun   
12          12 2017-10-14  12:30  Premier League     Matchweek 8  Sat   
13          13 2017-10-17  20:45    Champions Lg     Group stage  Tue   
14          14 2017-10-22  16:00  Premier League     Matchweek 9  Sun   
15          15 2017-10-28  15:00  Premier League    Matchweek 10  Sat   
16          16 2017-11-01  19:45    Champions Lg     Group stage  Wed   
17          17 2017-11-04  17:30  Premier League    Matchweek 11  Sat   
18          18 2017-11-18  15:00  Premier League    Matchweek 12  Sat   
19          19 2017-11-21  20:45    Champions Lg     Group stage  Tue   
20          20 2017-11-25  17:30  Premier League    Matchweek 13  Sat   
21          21 2017-11-29  20:00  Premier League    Matchweek 14  Wed   
22          22 2017-12-02  15:00  Premier League    Matchweek 15  Sat   
23          23 2017-12-06  19:45    Champions Lg     Group stage  Wed   
24          24 2017-12-10  14:15  Premier League    Matchweek 16  Sun   
25          25 2017-12-13  20:00  Premier League    Matchweek 17  Wed   
26          26 2017-12-17  16:30  Premier League    Matchweek 18  Sun   
27          27 2017-12-22  19:45  Premier League    Matchweek 19  Fri   
28          28 2017-12-26  17:30  Premier League    Matchweek 20  Tue   
29          29 2017-12-30  15:00  Premier League    Matchweek 21  Sat   
30          30 2018-01-01  15:00  Premier League    Matchweek 22  Mon   
31          31 2018-01-05  19:55          FA Cup     Third round  Fri   
32          32 2018-01-14  16:00  Premier League    Matchweek 23  Sun   
33          33 2018-01-22  20:00  Premier League    Matchweek 24  Mon   
34          34 2018-01-27  19:45          FA Cup    Fourth round  Sat   
35          35 2018-01-30  20:00  Premier League    Matchweek 25  Tue   
36          36 2018-02-04  16:30  Premier League    Matchweek 26  Sun   
37          37 2018-02-11  16:30  Premier League    Matchweek 27  Sun   
38          38 2018-02-14  19:45    Champions Lg     Round of 16  Wed   
39          39 2018-02-24  15:00  Premier League    Matchweek 28  Sat   
40          40 2018-03-03  17:30  Premier League    Matchweek 29  Sat   
41          41 2018-03-06  19:45    Champions Lg     Round of 16  Tue   
42          42 2018-03-10  12:30  Premier League    Matchweek 30  Sat   
43          43 2018-03-17  17:30  Premier League    Matchweek 31  Sat   
44          44 2018-03-31  12:30  Premier League    Matchweek 32  Sat   
45          45 2018-04-04  19:45    Champions Lg  Quarter-finals  Wed   
46          46 2018-04-07  12:30  Premier League    Matchweek 33  Sat   
47          47 2018-04-10  19:45    Champions Lg  Quarter-finals  Tue   
48          48 2018-04-14  17:30  Premier League    Matchweek 34  Sat   
49          49 2018-04-21  12:30  Premier League    Matchweek 35  Sat   
50          50 2018-04-24  19:45    Champions Lg     Semi-finals  Tue   
51          51 2018-04-28  12:30  Premier League    Matchweek 36  Sat   
52          52 2018-05-02  20:45    Champions Lg     Semi-finals  Wed   
53          53 2018-05-06  16:30  Premier League    Matchweek 

In [191]:
rolling_average_or_sum(df,cols=['Points','Win','Draw','Lose','GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss','Poss'],window=3,agg_func='mean')

Unnamed: 0       Date   Time            Comp           Round  Day  \
0            0 2017-08-12  12:30  Premier League     Matchweek 1  Sat   
1            1 2017-08-15  20:45    Champions Lg  Play-off round  Tue   
2            2 2017-08-19  15:00  Premier League     Matchweek 2  Sat   
3            3 2017-08-23  19:45    Champions Lg  Play-off round  Wed   
4            4 2017-08-27  16:00  Premier League     Matchweek 3  Sun   
5            5 2017-09-09  12:30  Premier League     Matchweek 4  Sat   
6            6 2017-09-13  19:45    Champions Lg     Group stage  Wed   
7            7 2017-09-16  15:00  Premier League     Matchweek 5  Sat   
8            8 2017-09-19  19:45         EFL Cup     Third round  Tue   
9            9 2017-09-23  17:30  Premier League     Matchweek 6  Sat   
10          10 2017-09-26  21:45    Champions Lg     Group stage  Tue   
11          11 2017-10-01  16:30  Premier League     Matchweek 7  Sun   
12          12 2017-10-14  12:30  Premier League     Matchweek 8  Sat   
13          13 2017-10-17  20:45    Champions Lg     Group stage  Tue   
14          14 2017-10-22  16:00  Premier League     Matchweek 9  Sun   
15          15 2017-10-28  15:00  Premier League    Matchweek 10  Sat   
16          16 2017-11-01  19:45    Champions Lg     Group stage  Wed   
17          17 2017-11-04  17:30  Premier League    Matchweek 11  Sat   
18          18 2017-11-18  15:00  Premier League    Matchweek 12  Sat   
19          19 2017-11-21  20:45    Champions Lg     Group stage  Tue   
20          20 2017-11-25  17:30  Premier League    Matchweek 13  Sat   
21          21 2017-11-29  20:00  Premier League    Matchweek 14  Wed   
22          22 2017-12-02  15:00  Premier League    Matchweek 15  Sat   
23          23 2017-12-06  19:45    Champions Lg     Group stage  Wed   
24          24 2017-12-10  14:15  Premier League    Matchweek 16  Sun   
25          25 2017-12-13  20:00  Premier League    Matchweek 17  Wed   
26          26 2017-12-17  16:30  Premier League    Matchweek 18  Sun   
27          27 2017-12-22  19:45  Premier League    Matchweek 19  Fri   
28          28 2017-12-26  17:30  Premier League    Matchweek 20  Tue   
29          29 2017-12-30  15:00  Premier League    Matchweek 21  Sat   
30          30 2018-01-01  15:00  Premier League    Matchweek 22  Mon   
31          31 2018-01-05  19:55          FA Cup     Third round  Fri   
32          32 2018-01-14  16:00  Premier League    Matchweek 23  Sun   
33          33 2018-01-22  20:00  Premier League    Matchweek 24  Mon   
34          34 2018-01-27  19:45          FA Cup    Fourth round  Sat   
35          35 2018-01-30  20:00  Premier League    Matchweek 25  Tue   
36          36 2018-02-04  16:30  Premier League    Matchweek 26  Sun   
37          37 2018-02-11  16:30  Premier League    Matchweek 27  Sun   
38          38 2018-02-14  19:45    Champions Lg     Round of 16  Wed   
39          39 2018-02-24  15:00  Premier League    Matchweek 28  Sat   
40          40 2018-03-03  17:30  Premier League    Matchweek 29  Sat   
41          41 2018-03-06  19:45    Champions Lg     Round of 16  Tue   
42          42 2018-03-10  12:30  Premier League    Matchweek 30  Sat   
43          43 2018-03-17  17:30  Premier League    Matchweek 31  Sat   
44          44 2018-03-31  12:30  Premier League    Matchweek 32  Sat   
45          45 2018-04-04  19:45    Champions Lg  Quarter-finals  Wed   
46          46 2018-04-07  12:30  Premier League    Matchweek 33  Sat   
47          47 2018-04-10  19:45    Champions Lg  Quarter-finals  Tue   
48          48 2018-04-14  17:30  Premier League    Matchweek 34  Sat   
49          49 2018-04-21  12:30  Premier League    Matchweek 35  Sat   
50          50 2018-04-24  19:45    Champions Lg     Semi-finals  Tue   
51          51 2018-04-28  12:30  Premier League    Matchweek 36  Sat   
52          52 2018-05-02  20:45    Champions Lg     Semi-finals  Wed   
53          53 2018-05-06  16:30  Premier League    Matchweek 

In [154]:
df[['a','b']] = df[['Result','Points','Total_Points']].expanding().mean()

In [166]:
df[['Points','Win','Draw','Lose']].shift(1).cumsum()

Points   Win  Draw  Lose
0      NaN   NaN   NaN   NaN
1      1.0   0.0   1.0   0.0
2      4.0   1.0   1.0   0.0
3      7.0   2.0   1.0   0.0
4     10.0   3.0   1.0   0.0
5     13.0   4.0   1.0   0.0
6     13.0   4.0   1.0   1.0
7     14.0   4.0   2.0   1.0
8     15.0   4.0   3.0   1.0
9     15.0   4.0   3.0   2.0
10    18.0   5.0   3.0   2.0
11    19.0   5.0   4.0   2.0
12    20.0   5.0   5.0   2.0
13    21.0   5.0   6.0   2.0
14    24.0   6.0   6.0   2.0
15    24.0   6.0   6.0   3.0
16    27.0   7.0   6.0   3.0
17    30.0   8.0   6.0   3.0
18    33.0   9.0   6.0   3.0
19    36.0  10.0   6.0   3.0
20    37.0  10.0   7.0   3.0
21    38.0  10.0   8.0   3.0
22    41.0  11.0   8.0   3.0
23    44.0  12.0   8.0   3.0
24    47.0  13.0   8.0   3.0
25    48.0  13.0   9.0   3.0
26    49.0  13.0  10.0   3.0
27    52.0  14.0  10.0   3.0
28    53.0  14.0  11.0   3.0
29    56.0  15.0  11.0   3.0
30    59.0  16.0  11.0   3.0
31    62.0  17.0  11.0   3.0
32    65.0  18.0  11.0   3.0
33    68.0  19.0  11.0   3.0
34    68.0  19.0  11.0   4.0
35    68.0  19.0  11.0   5.0
36    71.0  20.0  11.0   5.0
37    72.0  20.0  12.0   5.0
38    75.0  21.0  12.0   5.0
39    78.0  22.0  12.0   5.0
40    81.0  23.0  12.0   5.0
41    84.0  24.0  12.0   5.0
42    85.0  24.0  13.0   5.0
43    85.0  24.0  13.0   6.0
44    88.0  25.0  13.0   6.0
45    91.0  26.0  13.0   6.0
46    94.0  27.0  13.0   6.0
47    95.0  27.0  14.0   6.0
48    98.0  28.0  14.0   6.0
49   101.0  29.0  14.0   6.0
50   102.0  29.0  15.0   6.0
51   105.0  30.0  15.0   6.0
52   106.0  30.0  16.0   6.0
53   106.0  30.0  16.0   7.0
54   106.0  30.0  16.0   8.0
55   109.0  31.0  16.0   8.0

In [164]:
a1 = df[['Points','Win','Draw','Lose']].shift(1).rolling(1).sum()

In [165]:
a1

Points  Win  Draw  Lose
0      NaN  NaN   NaN   NaN
1      1.0  0.0   1.0   0.0
2      3.0  1.0   0.0   0.0
3      3.0  1.0   0.0   0.0
4      3.0  1.0   0.0   0.0
5      3.0  1.0   0.0   0.0
6      0.0  0.0   0.0   1.0
7      1.0  0.0   1.0   0.0
8      1.0  0.0   1.0   0.0
9      0.0  0.0   0.0   1.0
10     3.0  1.0   0.0   0.0
11     1.0  0.0   1.0   0.0
12     1.0  0.0   1.0   0.0
13     1.0  0.0   1.0   0.0
14     3.0  1.0   0.0   0.0
15     0.0  0.0   0.0   1.0
16     3.0  1.0   0.0   0.0
17     3.0  1.0   0.0   0.0
18     3.0  1.0   0.0   0.0
19     3.0  1.0   0.0   0.0
20     1.0  0.0   1.0   0.0
21     1.0  0.0   1.0   0.0
22     3.0  1.0   0.0   0.0
23     3.0  1.0   0.0   0.0
24     3.0  1.0   0.0   0.0
25     1.0  0.0   1.0   0.0
26     1.0  0.0   1.0   0.0
27     3.0  1.0   0.0   0.0
28     1.0  0.0   1.0   0.0
29     3.0  1.0   0.0   0.0
30     3.0  1.0   0.0   0.0
31     3.0  1.0   0.0   0.0
32     3.0  1.0   0.0   0.0
33     3.0  1.0   0.0   0.0
34     0.0  0.0   0.0   1.0
35     0.0  0.0   0.0   1.0
36     3.0  1.0   0.0   0.0
37     1.0  0.0   1.0   0.0
38     3.0  1.0   0.0   0.0
39     3.0  1.0   0.0   0.0
40     3.0  1.0   0.0   0.0
41     3.0  1.0   0.0   0.0
42     1.0  0.0   1.0   0.0
43     0.0  0.0   0.0   1.0
44     3.0  1.0   0.0   0.0
45     3.0  1.0   0.0   0.0
46     3.0  1.0   0.0   0.0
47     1.0  0.0   1.0   0.0
48     3.0  1.0   0.0   0.0
49     3.0  1.0   0.0   0.0
50     1.0  0.0   1.0   0.0
51     3.0  1.0   0.0   0.0
52     1.0  0.0   1.0   0.0
53     0.0  0.0   0.0   1.0
54     0.0  0.0   0.0   1.0
55     3.0  1.0   0.0   0.0

In [146]:
df.Lose.shift(1).expanding().mean()

0          NaN
1     0.000000
2     0.000000
3     0.000000
4     0.000000
5     0.000000
6     0.166667
7     0.142857
8     0.125000
9     0.222222
10    0.200000
11    0.181818
12    0.166667
13    0.153846
14    0.142857
15    0.200000
16    0.187500
17    0.176471
18    0.166667
19    0.157895
20    0.150000
21    0.142857
22    0.136364
23    0.130435
24    0.125000
25    0.120000
26    0.115385
27    0.111111
28    0.107143
29    0.103448
30    0.100000
31    0.096774
32    0.093750
33    0.090909
34    0.117647
35    0.142857
36    0.138889
37    0.135135
38    0.131579
39    0.128205
40    0.125000
41    0.121951
42    0.119048
43    0.139535
44    0.136364
45    0.133333
46    0.130435
47    0.127660
48    0.125000
49    0.122449
50    0.120000
51    0.117647
52    0.115385
53    0.132075
54    0.148148
55    0.145455
Name: Lose, dtype: float64

In [83]:
df['Win'] = df.apply(lambda x : 1 if x.Result == 'W' else 0 ,axis=1)
df['Draw'] = df.apply(lambda x : 1 if x.Result == 'D' else 0 ,axis=1)
df['Lose'] = df.apply(lambda x : 1 if x.Result == 'L' else 0 ,axis=1)

In [84]:
df['Away_Win'] = df.apply(lambda x : 1 if x.Venue == 'Away' and x.Result == 'W' else 0 ,axis=1)
df['Away_Draw'] = df.apply(lambda x : 1 if x.Venue == 'Away' and x.Result == 'D' else 0 ,axis=1)
df['Away_Loss'] = df.apply(lambda x : 1 if x.Venue == 'Away' and x.Result == 'L' else 0 ,axis=1)

In [85]:
df['Home_Win'] = df.apply(lambda x : 1 if x.Venue == 'Home' and x.Result == 'W' else 0 ,axis=1)
df['Home_Draw'] = df.apply(lambda x : 1 if x.Venue == 'Home' and x.Result == 'D' else 0 ,axis=1)
df['Home_Loss'] = df.apply(lambda x : 1 if x.Venue == 'Home' and x.Result == 'L' else 0 ,axis=1)

In [86]:
pd.DataFrame(df.groupby(['Venue','Result'])['Result'].agg('count'))

Result
Venue   Result        
Away    D            7
        L            7
        W           13
Home    D            9
        L            1
        W           18
Neutral L            1

In [107]:
pd.DataFrame(df.groupby(['Captain','Result'])['Result'].agg('count'))

Result
Captain           Result        
Alberto Moreno    L            1
Dejan Lovren      W            1
Emre Can          L            1
                  W            1
James Milner      D            1
                  L            2
                  W            6
Jordan Henderson  D           14
                  L            5
                  W           18
Philippe Coutinho D            1
                  W            2
Simon Mignolet    W            3

In [87]:
df[['Venue','Result','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss']].head()#.describe()*100

Venue Result  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  Home_Loss
0  Away      D         0          1          0         0          0          0
1  Away      W         1          0          0         0          0          0
2  Home      W         0          0          0         1          0          0
3  Home      W         0          0          0         1          0          0
4  Home      W         0          0          0         1          0          0

In [88]:
df.Away_Loss.value_counts()

0    49
1     7
Name: Away_Loss, dtype: int64

In [50]:
cols = ['GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'] 
gp = df.groupby(['Month'])[cols]#.index#iloc[12]#.to_dict()
gp_arr =  []
for g,gd in gp:
    print(g)
    print()
    gd_cum = gd.shift(1).expanding().mean()
    display(gd_cum)
    gp_arr.append(gd_cum)
    print()

1



GF    GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  \
23       NaN   NaN       NaN        NaN        NaN       NaN        NaN   
24  1.000000  2.00       0.0   0.000000   0.000000       0.0        0.0   
25  0.500000  1.50       0.0   0.000000   0.500000       0.0        0.0   
26  0.333333  1.00       0.0   0.333333   0.333333       0.0        0.0   
27  0.250000  1.25       0.0   0.250000   0.250000       0.0        0.0   

    Home_Loss  
23        NaN  
24   1.000000  
25   0.500000  
26   0.333333  
27   0.500000


2



GF   GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  Home_Loss
28  NaN  NaN       NaN        NaN        NaN       NaN        NaN        NaN
29  1.0  0.0       1.0        0.0        0.0       0.0        0.0        0.0
30  1.5  0.5       0.5        0.0        0.0       0.5        0.0        0.0


3



...

GF    GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  \
8        NaN   NaN       NaN        NaN        NaN       NaN        NaN   
9   0.000000  0.00       0.0   1.000000        0.0  0.000000   0.000000   
10  1.000000  1.00       0.0   0.500000        0.0  0.000000   0.500000   
11  1.666667  1.00       0.0   0.333333        0.0  0.333333   0.333333   
12  1.750000  0.75       0.0   0.250000        0.0  0.500000   0.250000   

    Home_Loss  
8         NaN  
9         0.0  
10        0.0  
11        0.0  
12        0.0


11



GF   GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  Home_Loss
13  NaN  NaN       NaN        NaN        NaN       NaN        NaN        NaN
14  1.0  0.0       0.0        0.0        0.0       1.0        0.0        0.0
15  0.5  2.0       0.0        0.0        0.5       0.5        0.0        0.0


12



GF        GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  \
16       NaN       NaN       NaN        NaN        NaN       NaN        NaN   
17  2.000000  3.000000  0.000000        0.0   1.000000  0.000000        0.0   
18  1.500000  2.500000  0.000000        0.0   1.000000  0.000000        0.0   
19  2.000000  1.666667  0.000000        0.0   0.666667  0.333333        0.0   
20  2.000000  1.250000  0.000000        0.0   0.500000  0.500000        0.0   
21  2.400000  1.200000  0.200000        0.0   0.400000  0.400000        0.0   
22  2.833333  1.166667  0.166667        0.0   0.333333  0.500000        0.0   

    Home_Loss  
16        NaN  
17        0.0  
18        0.0  
19        0.0  
20        0.0  
21        0.0  
22        0.0

In [177]:
cum = pd.concat(gp_arr)

In [179]:
cum[cum.index==2]

GF   GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  Home_Loss
2  4.0  1.0       0.0        0.0        0.0       1.0        1.0        0.0

In [176]:
cum.sort_index()

GF   GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  Home_Loss
0   NaN  NaN       NaN        NaN        NaN       NaN        NaN        NaN
1   1.0  1.0       0.0        0.0        0.0       0.0        1.0        0.0
2   4.0  1.0       0.0        0.0        0.0       1.0        1.0        0.0
3   6.0  1.0       1.0        0.0        0.0       1.0        1.0        0.0
4   NaN  NaN       NaN        NaN        NaN       NaN        NaN        NaN
..  ...  ...       ...        ...        ...       ...        ...        ...
56  0.0  1.0       0.0        0.0        1.0       0.0        0.0        0.0
57  2.0  3.0       0.0        0.0        1.0       0.0        1.0        0.0
58  5.0  3.0       1.0        0.0        1.0       0.0        1.0        0.0
59  5.0  3.0       1.0        0.0        1.0       0.0        2.0        0.0
60  6.0  4.0       1.0        0.0        1.0       0.0        3.0        0.0

[61 rows x 8 columns]

In [51]:
cols = ['GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'] 
gp = df.groupby(['Month'])[cols]#.index#iloc[12]#.to_dict()
for g,gd in gp:
    print(g)
    print()
    display(gd.shift(1))
    print()

1



GF   GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  Home_Loss
23  NaN  NaN       NaN        NaN        NaN       NaN        NaN        NaN
24  1.0  2.0       0.0        0.0        0.0       0.0        0.0        1.0
25  0.0  1.0       0.0        0.0        1.0       0.0        0.0        0.0
26  0.0  0.0       0.0        1.0        0.0       0.0        0.0        0.0
27  0.0  2.0       0.0        0.0        0.0       0.0        0.0        1.0


2



GF   GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  Home_Loss
28  NaN  NaN       NaN        NaN        NaN       NaN        NaN        NaN
29  1.0  0.0       1.0        0.0        0.0       0.0        0.0        0.0
30  2.0  1.0       0.0        0.0        0.0       1.0        0.0        0.0


3



...

GF   GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  Home_Loss
8   NaN  NaN       NaN        NaN        NaN       NaN        NaN        NaN
9   0.0  0.0       0.0        1.0        0.0       0.0        0.0        0.0
10  2.0  2.0       0.0        0.0        0.0       0.0        1.0        0.0
11  3.0  1.0       0.0        0.0        0.0       1.0        0.0        0.0
12  2.0  0.0       0.0        0.0        0.0       1.0        0.0        0.0


11



GF   GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  Home_Loss
13  NaN  NaN       NaN        NaN        NaN       NaN        NaN        NaN
14  1.0  0.0       0.0        0.0        0.0       1.0        0.0        0.0
15  0.0  4.0       0.0        0.0        1.0       0.0        0.0        0.0


12



GF   GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  Home_Loss
16  NaN  NaN       NaN        NaN        NaN       NaN        NaN        NaN
17  2.0  3.0       0.0        0.0        1.0       0.0        0.0        0.0
18  1.0  2.0       0.0        0.0        1.0       0.0        0.0        0.0
19  3.0  0.0       0.0        0.0        0.0       1.0        0.0        0.0
20  2.0  0.0       0.0        0.0        0.0       1.0        0.0        0.0
21  4.0  1.0       1.0        0.0        0.0       0.0        0.0        0.0
22  5.0  1.0       0.0        0.0        0.0       1.0        0.0        0.0

In [105]:
m = df.groupby("Month")[cols].agg('sum')
#m['Rank_Month'] = df.Month.unique()
#group_jan = grouped_months.get_group(0)

In [106]:
m.index=df.Month.unique()

In [107]:
m_s = m.shift(1)
m_s.columns = new_cols

In [108]:
m_s

prev_month_GF  prev_month_GA  prev_month_Away_Win  prev_month_Away_Draw  \
8             NaN            NaN                  NaN                   NaN   
9            13.0            5.0                  1.0                   1.0   
10            5.0            1.0                  1.0                   0.0   
11           15.0            4.0                  5.0                   0.0   
12           17.0           14.0                  2.0                   1.0   
1             8.0            5.0                  1.0                   0.0   
2             7.0            2.0                  1.0                   1.0   
3             8.0            3.0                  1.0                   0.0   
4            19.0            2.0                  2.0                   0.0   
5            10.0            2.0                  2.0                   0.0   

    prev_month_Away_Loss  prev_month_Home_Win  prev_month_Home_Draw  \
8                    NaN                  NaN                   NaN   
9                    1.0                  3.0                   1.0   
10                   0.0                  2.0                   1.0   
11                   0.0                  1.0                   0.0   
12                   0.0                  2.0                   0.0   
1                    1.0                  1.0                   3.0   
2                    0.0                  1.0                   1.0   
3                    1.0                  2.0                   1.0   
4                    0.0                  3.0                   1.0   
5                    0.0                  1.0                   2.0   

    prev_month_Home_Loss  
8                    NaN  
9                    0.0  
10                   0.0  
11                   0.0  
12                   3.0  
1                    0.0  
2                    0.0  
3                    1.0  
4                    0.0  
5                    0.0

In [86]:
.shift(1)

Int64Index([1, 2, 3, 4, 5, 8, 9, 10, 11, 12], dtype='int64', name='Month')

In [89]:
df.Month.unique()

array([ 8,  9, 10, 11, 12,  1,  2,  3,  4,  5], dtype=int64)

In [ ]:
month_df.columns = new_cols

In [109]:
aa= pd.merge(df,m_s,left_on = 'Month',right_on=m_s.index)

In [110]:
aa

Unnamed: 0       Date   Time            Comp           Round  Day Venue  \
0            0 2021-08-11  20:00       Super Cup  UEFA Super Cup  Wed  Home   
1            1 2021-08-14  15:00  Premier League     Matchweek 1  Sat  Home   
2            2 2021-08-22  16:30  Premier League     Matchweek 2  Sun  Away   
3            3 2021-08-28  17:30  Premier League     Matchweek 3  Sat  Away   
4            4 2021-09-11  17:30  Premier League     Matchweek 4  Sat  Home   
..         ...        ...    ...             ...             ...  ...   ...   
56          56 2022-05-07  15:00  Premier League    Matchweek 36  Sat  Home   
57          57 2022-05-11  19:30  Premier League    Matchweek 33  Wed  Away   
58          58 2022-05-14  16:45          FA Cup           Final  Sat  Home   
59          59 2022-05-19  20:00  Premier League    Matchweek 27  Thu  Home   
60          60 2022-05-22  16:00  Premier League    Matchweek 38  Sun  Home   

   Result  GF  GA        Opponent   xG  xGA  Poss  Attendance  \
0       D   1   1   es Villarreal  NaN  NaN    62         NaN   
1       W   3   0  Crystal Palace  0.9  0.3    62     38965.0   
2       W   2   0         Arsenal  2.9  0.3    65     58729.0   
3       D   1   1       Liverpool  0.8  2.6    35     54000.0   
4       W   3   0     Aston Villa  1.1  1.5    57     39969.0   
..    ...  ..  ..             ...  ...  ...   ...         ...   
56      D   2   2          Wolves  2.5  2.1    59     32190.0   
57      W   3   0    Leeds United  1.5  0.5    67     36549.0   
58      D   0   0       Liverpool  NaN  NaN    47     84897.0   
59      D   1   1  Leicester City  1.7  0.1    68     31478.0   
60      W   2   1         Watford  2.4  1.0    72     32089.0   

              Captain Formation         Referee  Match Report  \
0        N'Golo Kanté     3-4-3  Sergey Karasev  Match Report   
1   César Azpilicueta     3-4-3   Jonathan Moss  Match Report   
2   César Azpilicueta     3-4-3    Paul Tierney  Match Report   
3   César Azpilicueta     3-4-3  Anthony Taylor  Match Report   
4       Marcos Alonso     3-4-3  Stuart Attwell  Match Report   
..                ...       ...             ...           ...   
56  César Azpilicueta   3-4-1-2    Peter Bankes  Match Report   
57           Jorginho     3-4-3  Anthony Taylor  Match Report   
58           Jorginho     3-4-3    Craig Pawson  Match Report   
59           Jorginho     3-4-3  Stuart Attwell  Match Report   
60  César Azpilicueta     3-4-3       Mike Dean  Match Report   

                                                Notes     Team  Standard_Gls  \
0                                                 NaN  Chelsea             1   
1                                                 NaN  Chelsea             3   
2                                                 NaN  Chelsea             2   
3                                                 NaN  Chelsea             1   
4                                                 NaN  Chelsea             3   
..                                                ...      ...           ...   
56                                                NaN  Chelsea             2   
57                                                NaN  Chelsea             3   
58  Liverpool won on penalty kicks following extra...  Chelsea             0   
59                                                NaN  Chelsea             1   
60                                                NaN  Chelsea             2   

    Standard_Sh  Standard_SoT  Standard_SoT%  Standard_G/Sh  Standard_G/SoT  \
0            19             7           36.8           0.05            0.14   
1            13             6           46.2           0.23            0.50   
2            22             5           22.7           0.09            0.40   
3             6             2           33.3           0.17            0.50   
4            12             4           33.3           0.25            0.75   
..          ...           ...            ...            ..

In [52]:
def get_no_of_time_opp_faced(row):
    present_date = row.Prev_match_date
    if present_date is np.nan:
        pass
    back_df = df[df.Date<=present_date]
    Opp_faced = back_df.Opponent.value_counts().to_dict()
    if row.Opponent not  in Opp_faced.keys():
        return 0
    #display(Opp_faced)
    return Opp_faced[row.Opponent]

In [170]:
aa[cols].shift(1).cumsum()

GF    GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  \
0     NaN   NaN       NaN        NaN        NaN       NaN        NaN   
1     1.0   1.0       0.0        0.0        0.0       0.0        1.0   
2     4.0   1.0       0.0        0.0        0.0       1.0        1.0   
3     6.0   1.0       1.0        0.0        0.0       1.0        1.0   
4     7.0   2.0       1.0        1.0        0.0       1.0        1.0   
..    ...   ...       ...        ...        ...       ...        ...   
56  111.0  46.0      18.0        5.0        4.0      16.0        9.0   
57  113.0  48.0      18.0        5.0        4.0      16.0       10.0   
58  116.0  48.0      19.0        5.0        4.0      16.0       10.0   
59  116.0  48.0      19.0        5.0        4.0      16.0       11.0   
60  117.0  49.0      19.0        5.0        4.0      16.0       12.0   

    Home_Loss  
0         NaN  
1         0.0  
2         0.0  
3         0.0  
4         0.0  
..        ...  
56        4.0  
57        4.0  
58        4.0  
59        4.0  
60        4.0  

[61 rows x 8 columns]

In [61]:
cols = ['GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss']
alias = 'prev_month_'
new_cols = [alias+col for col in cols]

rolling_averages(grouped_months, cols, new_cols)

TypeError: 'DataFrameGroupBy' object does not support item assignment

In [93]:
def get_cum_by_col(df,grouper,grouper_name,cols,agg_func):
    df = df.copy()
    gp_arr=[]
    for g,gd in df.groupby([grouper])[cols]:
        #print(g)
        #display(gd)
        if agg_func == 'sum':
            gd_cum = gd.shift(1).cumsum()
        if agg_func == 'mean':
            gd_cum = gd.shift(1).expanding().mean()
        gp_arr.append(gd_cum)
    cum = pd.concat(gp_arr)
    cum = cum.sort_index()
    alias = '_this_'+grouper_name+'_'+agg_func
    cum_cols = [col+alias for col in cols]
    cum.columns = cum_cols
    df_with_cum = pd.concat([df,cum],axis=1)
    return df_with_cum

In [207]:
def previous_month_agg(df,cols,agg_func):
    df=df.copy()
    group_df = df.groupby("Month")[cols].agg(agg_func)
    
    #cummulative in each month
    gp_arr=[]
    for g,gd in df.groupby(['Month'])[cols]:
        #print(g)
        #display(gd)
        if agg_func == 'sum':
            gd_cum = gd.shift(1).cumsum()
        if agg_func == 'mean':
            gd_cum = gd.shift(1).expanding().mean()
        gp_arr.append(gd_cum)
    cum = pd.concat(gp_arr)
    cum = cum.sort_index()
    cum_cols = [col+'_this_month_'+agg_func for col in cols]
    cum.columns = cum_cols
    df_with_cum = pd.concat([df,cum],axis=1)
    
    group_df.index = df.Month.unique() 
    group_df = group_df.shift(1)
    alias1 = '_'+agg_func+'_prev_month_'
    new_cols = [col+alias1 for col in cols]
    group_df.columns = new_cols
    
    out_df= pd.merge(df_with_cum, group_df ,left_on = 'Month',right_on=group_df.index)
        
    return out_df

In [54]:
previous_month_agg(df,cols,'sum')

Month  GF  GA  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  \
0       8   0   2         0          0          1         0          0   
1       8   0   2         0          0          0         0          0   
2       8   6   0         1          0          0         0          0   
3       8   0   5         0          0          1         0          0   
4       9   1   0         0          0          0         1          0   
5       9   1   0         1          0          0         0          0   
6       9   3   0         0          0          0         1          0   
7       9   3   1         0          0          0         1          0   
8      10   0   0         0          1          0         0          0   
9      10   2   2         0          0          0         0          1   
10     10   3   1         0          0          0         1          0   
11     10   2   0         0          0          0         1          0   
12     10   2   0         1          0          0         0          0   
13     11   1   0         0          0          0         1          0   
14     11   0   4         0          0          1         0          0   
15     11   2   0         0          0          0         1          0   
16     12   2   3         0          0          1         0          0   
17     12   1   2         0          0          1         0          0   
18     12   3   0         0          0          0         1          0   
19     12   2   0         0          0          0         1          0   
20     12   4   1         1          0          0         0          0   
21     12   5   1         0          0          0         1          0   
22     12   5   0         1          0          0         0          0   
23      1   1   2         0          0          0         0          0   
24      1   0   1         0          0          1         0          0   
25      1   0   0         0          1          0         0          0   
26      1   0   2         0          0          0         0          0   
27      1   0   0         0          0          0         0          1   
28      2   1   0         1          0          0         0          0   
29      2   2   1         0          0          0         1          0   
30      2   2   1         0          0          0         1          0   
31      3   3   2         1          0          0         0          0   
32      3   2   0         0          0          0         1          0   
33      3   0   2         0          0          0         0          0   
34      3   1   0         1          0          0         0          0   
35      4   0   3         0          0          1         0          0   
36      4   1   2         0          0          0         0          0   
37      4   0   1         0          0          1         0          0   
38      4   4   2         1          0          0         0          0   
39      4   3   1         0          0          0         1          0   
40      5   2   1         1          0          0         0          0   
41      5   2   1         0          0          0         1          0   
42      5   0   3         0          0          1         0          0   
43      5   0   2         0          0          1         0          0   
44      5   5   1         0          0          0         1          0   

    Home_Loss  GF_this_month_sum  GA_this_month_sum  Away_Win_this_month_sum  \
0           0                NaN                NaN                      NaN   
1           1                0.0                2.0                      0.0   
2           0                0.0                4.0                      0.0   
3           0                6.0                4.0                      1.0   
4           0                NaN                NaN                      NaN   
5           0                1.0                0.0                      0.0   
6           0                2.0       

In [55]:
previous_month_agg(df=df,cols=['GF','GA'],agg_func='mean')

Month  GF  GA  GF_this_month_mean  GA_this_month_mean  \
0       8   0   2                 NaN                 NaN   
1       8   0   2            0.000000            2.000000   
2       8   6   0            0.000000            2.000000   
3       8   0   5            2.000000            1.333333   
4       9   1   0                 NaN                 NaN   
5       9   1   0            1.000000            0.000000   
6       9   3   0            1.000000            0.000000   
7       9   3   1            1.666667            0.000000   
8      10   0   0                 NaN                 NaN   
9      10   2   2            0.000000            0.000000   
10     10   3   1            1.000000            1.000000   
11     10   2   0            1.666667            1.000000   
12     10   2   0            1.750000            0.750000   
13     11   1   0                 NaN                 NaN   
14     11   0   4            1.000000            0.000000   
15     11   2   0            0.500000            2.000000   
16     12   2   3                 NaN                 NaN   
17     12   1   2            2.000000            3.000000   
18     12   3   0            1.500000            2.500000   
19     12   2   0            2.000000            1.666667   
20     12   4   1            2.000000            1.250000   
21     12   5   1            2.400000            1.200000   
22     12   5   0            2.833333            1.166667   
23      1   1   2                 NaN                 NaN   
24      1   0   1            1.000000            2.000000   
25      1   0   0            0.500000            1.500000   
26      1   0   2            0.333333            1.000000   
27      1   0   0            0.250000            1.250000   
28      2   1   0                 NaN                 NaN   
29      2   2   1            1.000000            0.000000   
30      2   2   1            1.500000            0.500000   
31      3   3   2                 NaN                 NaN   
32      3   2   0            3.000000            2.000000   
33      3   0   2            2.500000            1.000000   
34      3   1   0            1.666667            1.333333   
35      4   0   3                 NaN                 NaN   
36      4   1   2            0.000000            3.000000   
37      4   0   1            0.500000            2.500000   
38      4   4   2            0.333333            2.000000   
39      4   3   1            1.250000            2.000000   
40      5   2   1                 NaN                 NaN   
41      5   2   1            2.000000            1.000000   
42      5   0   3            2.000000            1.000000   
43      5   0   2            1.333333            1.666667   
44      5   5   1            1.000000            1.750000   

    GF_mean_prev_month_  GA_mean_prev_month_  
0                   NaN                  NaN  
1                   NaN                  NaN  
2                   NaN                  NaN  
3                   NaN                  NaN  
4              0.200000             1.000000  
5              0.200000             1.000000  
6              0.200000             1.000000  
7              0.200000             1.000000  
8              1.666667             0.666667  
9              1.666667             0.666667  
10             1.666667             0.666667  
11             1.666667             0.666667  
12             1.666667             0.666667  
13             1.500000             1.000000  
14             1.500000             1.000000  
15             1.500000             1.000000  
16             1.600000             1.800000  
17             1.600000             1.800000  
18             1.600000             1.800000  
19             1.600000             1.800000  
20             1.600000             1.800000  
21             1.600000             1.800000  
22             1.600000             1.800000  
23             1.800000             1.600000  
24             1.80000

In [56]:
previous_month_agg(df=df,cols=['Poss'],agg_func='mean')

Month  Poss  Poss_this_month_mean  Poss_mean_prev_month_
0       8    66                   NaN                    NaN
1       8    35             66.000000                    NaN
2       8    75             50.500000                    NaN
3       8    20             58.666667                    NaN
4       9    52                   NaN                   47.8
5       9    54             52.000000                   47.8
6       9    62             53.000000                   47.8
7       9    46             56.000000                   47.8
8      10    41                   NaN                   54.0
9      10    55             41.000000                   54.0
10     10    54             48.000000                   54.0
11     10    45             50.000000                   54.0
12     10    36             48.750000                   54.0
13     11    60                   NaN                   51.5
14     11    37             60.000000                   51.5
15     11    65             48.500000                   51.5
16     12    55                   NaN                   58.8
17     12    63             55.000000                   58.8
18     12    61             59.000000                   58.8
19     12    55             59.666667                   58.8
20     12    49             58.500000                   58.8
21     12    68             56.600000                   58.8
22     12    64             58.500000                   58.8
23      1    30                   NaN                   54.6
24      1    67             30.000000                   54.6
25      1    22             48.500000                   54.6
26      1    46             39.666667                   54.6
27      1    74             41.250000                   54.6
28      2    40                   NaN                   49.0
29      2    67             40.000000                   49.0
30      2    55             53.500000                   49.0
31      3    56                   NaN                   53.5
32      3    46             56.000000                   53.5
33      3    50             51.000000                   53.5
34      3    54             50.666667                   53.5
35      4    67                   NaN                   46.2
36      4    63             67.000000                   46.2
37      4    75             65.000000                   46.2
38      4    34             68.333333                   46.2
39      4    55             59.750000                   46.2
40      5    44                   NaN                   54.0
41      5    65             44.000000                   54.0
42      5    43             54.500000                   54.0
43      5    48             50.666667                   54.0
44      5    73             50.000000                   54.0

In [98]:
pd.DataFrame(df.groupby(['Venue','Result'])['Poss'].agg('mean'))

Poss
Venue   Result           
Away    D       55.142857
        L       58.857143
        W       55.230769
Home    D       61.666667
        L       69.000000
        W       58.277778
Neutral L       35.000000

## Possession
* Chelsea kept more possesion on road games but ended up in losing effort

In [58]:
pd.DataFrame(df.groupby(['Venue'])['Poss'].agg('mean'))

Poss
Venue           
Away   50.454545
Home   55.739130

In [97]:
pd.DataFrame(df.groupby(['Formation'])['Poss'].agg('mean'))

Poss
Formation           
3-5-1-1    57.000000
4-2-3-1    58.800000
4-3-3      57.130435
4-4-1-1    71.000000
4-4-2      58.000000

In [95]:
#cols = ['GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'] 
gp = df.groupby(['Venue'])['Poss']#.index#iloc[12]#.to_dict()
for g,gd in gp:
    print(g)
    print()
    display(gd.shift(1).expanding().mean())
    print()

Away



0           NaN
1     54.000000
5     45.500000
8     42.000000
9     49.000000
10    50.000000
11    52.333333
13    54.571429
14    56.500000
17    57.222222
19    56.700000
21    54.272727
22    54.666667
26    54.846154
27    54.928571
30    54.333333
33    54.500000
35    55.470588
37    56.500000
38    56.000000
42    55.950000
44    56.476190
46    57.000000
47    57.260870
49    56.208333
52    56.400000
53    55.769231
Name: Poss, dtype: float64


Home



2           NaN
3     71.000000
4     58.000000
6     55.000000
7     53.500000
12    57.200000
15    58.000000
16    60.000000
18    61.875000
20    61.777778
23    61.000000
24    60.272727
25    61.833333
28    62.384615
29    61.857143
31    61.800000
32    61.750000
34    60.235294
36    60.722222
39    59.315789
40    59.700000
41    60.238095
43    60.454545
45    60.304348
48    59.208333
50    59.280000
51    58.884615
54    59.333333
Name: Poss, dtype: float64


Neutral



55   NaN
Name: Poss, dtype: float64

In [202]:
def Trim_Captain(df):
    df = df.copy()
    Cap_count = df['Captain'].value_counts() #Captain
    top2 = Cap_count.index[:2]
    df['Captain_Rank'] = df.apply(lambda x : 'Cap/Vice' if x.Captain in top2 else 'other' ,axis=1)
    return df

In [128]:
Trim_Captain(df)

Unnamed: 0       Date   Time            Comp           Round  Day  \
0            0 2017-08-12  12:30  Premier League     Matchweek 1  Sat   
1            1 2017-08-15  20:45    Champions Lg  Play-off round  Tue   
2            2 2017-08-19  15:00  Premier League     Matchweek 2  Sat   
3            3 2017-08-23  19:45    Champions Lg  Play-off round  Wed   
4            4 2017-08-27  16:00  Premier League     Matchweek 3  Sun   
5            5 2017-09-09  12:30  Premier League     Matchweek 4  Sat   
6            6 2017-09-13  19:45    Champions Lg     Group stage  Wed   
7            7 2017-09-16  15:00  Premier League     Matchweek 5  Sat   
8            8 2017-09-19  19:45         EFL Cup     Third round  Tue   
9            9 2017-09-23  17:30  Premier League     Matchweek 6  Sat   
10          10 2017-09-26  21:45    Champions Lg     Group stage  Tue   
11          11 2017-10-01  16:30  Premier League     Matchweek 7  Sun   
12          12 2017-10-14  12:30  Premier League     Matchweek 8  Sat   
13          13 2017-10-17  20:45    Champions Lg     Group stage  Tue   
14          14 2017-10-22  16:00  Premier League     Matchweek 9  Sun   
15          15 2017-10-28  15:00  Premier League    Matchweek 10  Sat   
16          16 2017-11-01  19:45    Champions Lg     Group stage  Wed   
17          17 2017-11-04  17:30  Premier League    Matchweek 11  Sat   
18          18 2017-11-18  15:00  Premier League    Matchweek 12  Sat   
19          19 2017-11-21  20:45    Champions Lg     Group stage  Tue   
20          20 2017-11-25  17:30  Premier League    Matchweek 13  Sat   
21          21 2017-11-29  20:00  Premier League    Matchweek 14  Wed   
22          22 2017-12-02  15:00  Premier League    Matchweek 15  Sat   
23          23 2017-12-06  19:45    Champions Lg     Group stage  Wed   
24          24 2017-12-10  14:15  Premier League    Matchweek 16  Sun   
25          25 2017-12-13  20:00  Premier League    Matchweek 17  Wed   
26          26 2017-12-17  16:30  Premier League    Matchweek 18  Sun   
27          27 2017-12-22  19:45  Premier League    Matchweek 19  Fri   
28          28 2017-12-26  17:30  Premier League    Matchweek 20  Tue   
29          29 2017-12-30  15:00  Premier League    Matchweek 21  Sat   
30          30 2018-01-01  15:00  Premier League    Matchweek 22  Mon   
31          31 2018-01-05  19:55          FA Cup     Third round  Fri   
32          32 2018-01-14  16:00  Premier League    Matchweek 23  Sun   
33          33 2018-01-22  20:00  Premier League    Matchweek 24  Mon   
34          34 2018-01-27  19:45          FA Cup    Fourth round  Sat   
35          35 2018-01-30  20:00  Premier League    Matchweek 25  Tue   
36          36 2018-02-04  16:30  Premier League    Matchweek 26  Sun   
37          37 2018-02-11  16:30  Premier League    Matchweek 27  Sun   
38          38 2018-02-14  19:45    Champions Lg     Round of 16  Wed   
39          39 2018-02-24  15:00  Premier League    Matchweek 28  Sat   
40          40 2018-03-03  17:30  Premier League    Matchweek 29  Sat   
41          41 2018-03-06  19:45    Champions Lg     Round of 16  Tue   
42          42 2018-03-10  12:30  Premier League    Matchweek 30  Sat   
43          43 2018-03-17  17:30  Premier League    Matchweek 31  Sat   
44          44 2018-03-31  12:30  Premier League    Matchweek 32  Sat   
45          45 2018-04-04  19:45    Champions Lg  Quarter-finals  Wed   
46          46 2018-04-07  12:30  Premier League    Matchweek 33  Sat   
47          47 2018-04-10  19:45    Champions Lg  Quarter-finals  Tue   
48          48 2018-04-14  17:30  Premier League    Matchweek 34  Sat   
49          49 2018-04-21  12:30  Premier League    Matchweek 35  Sat   
50          50 2018-04-24  19:45    Champions Lg     Semi-finals  Tue   
51          51 2018-04-28  12:30  Premier League    Matchweek 36  Sat   
52          52 2018-05-02  20:45    Champions Lg     Semi-finals  Wed   
53          53 2018-05-06  16:30  Premier League    Matchweek 

In [102]:
Cap_count = df.Captain.value_counts()

In [120]:
top2 = Cap_count.index[:2].to_list()

In [121]:
top2.reverse()

In [122]:
top2

['James Milner', 'Jordan Henderson']

In [192]:
def All_Transformation(df):
    df = df.copy()
    df['Month'] = df.Date.dt.month
    df.loc[:,'GA'] = df.GA.apply(to_int)
    df.loc[:,'GF'] = df.GF.apply(to_int)
    
    df['Win'] = df.apply(lambda x : 1 if x.Result == 'W' else 0 ,axis=1)
    df['Draw'] = df.apply(lambda x : 1 if x.Result == 'D' else 0 ,axis=1)
    df['Lose'] = df.apply(lambda x : 1 if x.Result == 'L' else 0 ,axis=1)
    
    #Table Like metrics
    df['Points'] = df.apply(lambda x : 3 if x.Result == 'W' else (1 if x.Result == 'D' else 0) ,axis=1)
    df['Total_Points'] = df.Points.shift(1).cumsum()
    df['Total_GF'] = df.GF.shift(1).cumsum()
    df['Total_GA'] = df.GA.shift(1).cumsum()
    df['Total_Win'] = df.Win.shift(1).cumsum()
    df['Total_Draw'] = df.Draw.shift(1).cumsum()
    df['Total_Loss'] = df.Lose.shift(1).cumsum()
    
    #Average Like metrics
    df['Points_Avg_for_szn'] = df.Points.shift(1).expanding().mean()
    df['GF_Avg_for_szn'] = df.GF.shift(1).expanding().mean()
    df['GA_Avg_for_szn'] = df.GA.shift(1).expanding().mean()
    df['Win_Avg_for_szn'] = df.Win.shift(1).expanding().mean()
    df['Draw_Avg_for_szn'] = df.Draw.shift(1).expanding().mean()
    df['Loss_Avg_for_szn'] = df.Lose.shift(1).expanding().mean()
    
    #Venue like metric
    df['Away_Win'] = df.apply(lambda x : 1 if x.Venue == 'Away' and x.Result == 'W' else 0 ,axis=1)
    df['Away_Draw'] = df.apply(lambda x : 1 if x.Venue == 'Away' and x.Result == 'D' else 0 ,axis=1)
    df['Away_Loss'] = df.apply(lambda x : 1 if x.Venue == 'Away' and x.Result == 'L' else 0 ,axis=1)
    df['Home_Win'] = df.apply(lambda x : 1 if x.Venue == 'Home' and x.Result == 'W' else 0 ,axis=1)
    df['Home_Draw'] = df.apply(lambda x : 1 if x.Venue == 'Home' and x.Result == 'D' else 0 ,axis=1)
    df['Home_Loss'] = df.apply(lambda x : 1 if x.Venue == 'Home' and x.Result == 'L' else 0 ,axis=1)
    
    #rolling metrics
    df = rolling_average_or_sum(df,
                                cols=['Points','Win','Draw','Lose','GF','GA',
                                      'Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'],
                                window=1,agg_func='sum')
    df = rolling_average_or_sum(df,cols=['Points','Win','Draw','Lose','GF','GA',
                                         'Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'],
                                window=2,agg_func='sum')
    df = rolling_average_or_sum(df,cols=['Points','Win','Draw','Lose','GF','GA',
                                         'Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss','Poss'],
                                window=3,agg_func='mean')
    #last games metric
    df['Prev_match_date'] = df.Date.shift(1)
    df['Rest'] = df.Date - df.Prev_match_date
    df['Prev_comp'] = df.Comp.shift(1)
    df['Prev_Opp'] = df.Opponent.shift(1)
    
    df.loc[:,'Played_Opp_X_times'] = df.apply( get_no_of_time_opp_faced,axis='columns')
    
    month_cols = cols = ['GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss']
    df = previous_month_agg(df,month_cols,'sum')
    df = previous_month_agg(df=df,cols=['GF','GA'],agg_func='mean')
    df = previous_month_agg(df=df,cols=['Poss'],agg_func='mean')
    df = Trim_Captain(df)
    df = get_cum_by_col(df,grouper='Venue',grouper_name='Venue',cols=['Poss','GF','GA'],agg_func='mean')
    df = get_cum_by_col(df,grouper='Venue',grouper_name='Venue',cols=['Win','Lose','Draw','GF','GA'],agg_func='sum')
    df = get_cum_by_col(df,grouper='Formation',grouper_name='Formation',cols=['Poss','GF','GA'],agg_func='mean')
    df = get_cum_by_col(df,grouper='Formation',grouper_name='Formation',cols=['Win','Lose','Draw','GF','GA'],agg_func='sum')
    df = get_cum_by_col(df,grouper='Opponent',grouper_name='Opp',cols=['Poss','GA','GF'],agg_func='mean')
    df = get_cum_by_col(df,grouper='Opponent',grouper_name='Opp',cols=['Win','Lose','Draw','GA','GF'],agg_func='sum')
    
    return df

In [100]:
get_cum_by_col(df,grouper='Venue',grouper_name='Venue',cols=['Poss','GF','GA'],agg_func='mean')

Unnamed: 0       Date   Time            Comp           Round  Day  \
0            0 2017-08-12  12:30  Premier League     Matchweek 1  Sat   
1            1 2017-08-15  20:45    Champions Lg  Play-off round  Tue   
2            2 2017-08-19  15:00  Premier League     Matchweek 2  Sat   
3            3 2017-08-23  19:45    Champions Lg  Play-off round  Wed   
4            4 2017-08-27  16:00  Premier League     Matchweek 3  Sun   
5            5 2017-09-09  12:30  Premier League     Matchweek 4  Sat   
6            6 2017-09-13  19:45    Champions Lg     Group stage  Wed   
7            7 2017-09-16  15:00  Premier League     Matchweek 5  Sat   
8            8 2017-09-19  19:45         EFL Cup     Third round  Tue   
9            9 2017-09-23  17:30  Premier League     Matchweek 6  Sat   
10          10 2017-09-26  21:45    Champions Lg     Group stage  Tue   
11          11 2017-10-01  16:30  Premier League     Matchweek 7  Sun   
12          12 2017-10-14  12:30  Premier League     Matchweek 8  Sat   
13          13 2017-10-17  20:45    Champions Lg     Group stage  Tue   
14          14 2017-10-22  16:00  Premier League     Matchweek 9  Sun   
15          15 2017-10-28  15:00  Premier League    Matchweek 10  Sat   
16          16 2017-11-01  19:45    Champions Lg     Group stage  Wed   
17          17 2017-11-04  17:30  Premier League    Matchweek 11  Sat   
18          18 2017-11-18  15:00  Premier League    Matchweek 12  Sat   
19          19 2017-11-21  20:45    Champions Lg     Group stage  Tue   
20          20 2017-11-25  17:30  Premier League    Matchweek 13  Sat   
21          21 2017-11-29  20:00  Premier League    Matchweek 14  Wed   
22          22 2017-12-02  15:00  Premier League    Matchweek 15  Sat   
23          23 2017-12-06  19:45    Champions Lg     Group stage  Wed   
24          24 2017-12-10  14:15  Premier League    Matchweek 16  Sun   
25          25 2017-12-13  20:00  Premier League    Matchweek 17  Wed   
26          26 2017-12-17  16:30  Premier League    Matchweek 18  Sun   
27          27 2017-12-22  19:45  Premier League    Matchweek 19  Fri   
28          28 2017-12-26  17:30  Premier League    Matchweek 20  Tue   
29          29 2017-12-30  15:00  Premier League    Matchweek 21  Sat   
30          30 2018-01-01  15:00  Premier League    Matchweek 22  Mon   
31          31 2018-01-05  19:55          FA Cup     Third round  Fri   
32          32 2018-01-14  16:00  Premier League    Matchweek 23  Sun   
33          33 2018-01-22  20:00  Premier League    Matchweek 24  Mon   
34          34 2018-01-27  19:45          FA Cup    Fourth round  Sat   
35          35 2018-01-30  20:00  Premier League    Matchweek 25  Tue   
36          36 2018-02-04  16:30  Premier League    Matchweek 26  Sun   
37          37 2018-02-11  16:30  Premier League    Matchweek 27  Sun   
38          38 2018-02-14  19:45    Champions Lg     Round of 16  Wed   
39          39 2018-02-24  15:00  Premier League    Matchweek 28  Sat   
40          40 2018-03-03  17:30  Premier League    Matchweek 29  Sat   
41          41 2018-03-06  19:45    Champions Lg     Round of 16  Tue   
42          42 2018-03-10  12:30  Premier League    Matchweek 30  Sat   
43          43 2018-03-17  17:30  Premier League    Matchweek 31  Sat   
44          44 2018-03-31  12:30  Premier League    Matchweek 32  Sat   
45          45 2018-04-04  19:45    Champions Lg  Quarter-finals  Wed   
46          46 2018-04-07  12:30  Premier League    Matchweek 33  Sat   
47          47 2018-04-10  19:45    Champions Lg  Quarter-finals  Tue   
48          48 2018-04-14  17:30  Premier League    Matchweek 34  Sat   
49          49 2018-04-21  12:30  Premier League    Matchweek 35  Sat   
50          50 2018-04-24  19:45    Champions Lg     Semi-finals  Tue   
51          51 2018-04-28  12:30  Premier League    Matchweek 36  Sat   
52          52 2018-05-02  20:45    Champions Lg     Semi-finals  Wed   
53          53 2018-05-06  16:30  Premier League    Matchweek 

In [99]:
get_cum_by_col(df,grouper='Formation',grouper_name='Formation',cols=['Poss'],agg_func='mean')

Unnamed: 0       Date   Time            Comp           Round  Day  \
0            0 2017-08-12  12:30  Premier League     Matchweek 1  Sat   
1            1 2017-08-15  20:45    Champions Lg  Play-off round  Tue   
2            2 2017-08-19  15:00  Premier League     Matchweek 2  Sat   
3            3 2017-08-23  19:45    Champions Lg  Play-off round  Wed   
4            4 2017-08-27  16:00  Premier League     Matchweek 3  Sun   
5            5 2017-09-09  12:30  Premier League     Matchweek 4  Sat   
6            6 2017-09-13  19:45    Champions Lg     Group stage  Wed   
7            7 2017-09-16  15:00  Premier League     Matchweek 5  Sat   
8            8 2017-09-19  19:45         EFL Cup     Third round  Tue   
9            9 2017-09-23  17:30  Premier League     Matchweek 6  Sat   
10          10 2017-09-26  21:45    Champions Lg     Group stage  Tue   
11          11 2017-10-01  16:30  Premier League     Matchweek 7  Sun   
12          12 2017-10-14  12:30  Premier League     Matchweek 8  Sat   
13          13 2017-10-17  20:45    Champions Lg     Group stage  Tue   
14          14 2017-10-22  16:00  Premier League     Matchweek 9  Sun   
15          15 2017-10-28  15:00  Premier League    Matchweek 10  Sat   
16          16 2017-11-01  19:45    Champions Lg     Group stage  Wed   
17          17 2017-11-04  17:30  Premier League    Matchweek 11  Sat   
18          18 2017-11-18  15:00  Premier League    Matchweek 12  Sat   
19          19 2017-11-21  20:45    Champions Lg     Group stage  Tue   
20          20 2017-11-25  17:30  Premier League    Matchweek 13  Sat   
21          21 2017-11-29  20:00  Premier League    Matchweek 14  Wed   
22          22 2017-12-02  15:00  Premier League    Matchweek 15  Sat   
23          23 2017-12-06  19:45    Champions Lg     Group stage  Wed   
24          24 2017-12-10  14:15  Premier League    Matchweek 16  Sun   
25          25 2017-12-13  20:00  Premier League    Matchweek 17  Wed   
26          26 2017-12-17  16:30  Premier League    Matchweek 18  Sun   
27          27 2017-12-22  19:45  Premier League    Matchweek 19  Fri   
28          28 2017-12-26  17:30  Premier League    Matchweek 20  Tue   
29          29 2017-12-30  15:00  Premier League    Matchweek 21  Sat   
30          30 2018-01-01  15:00  Premier League    Matchweek 22  Mon   
31          31 2018-01-05  19:55          FA Cup     Third round  Fri   
32          32 2018-01-14  16:00  Premier League    Matchweek 23  Sun   
33          33 2018-01-22  20:00  Premier League    Matchweek 24  Mon   
34          34 2018-01-27  19:45          FA Cup    Fourth round  Sat   
35          35 2018-01-30  20:00  Premier League    Matchweek 25  Tue   
36          36 2018-02-04  16:30  Premier League    Matchweek 26  Sun   
37          37 2018-02-11  16:30  Premier League    Matchweek 27  Sun   
38          38 2018-02-14  19:45    Champions Lg     Round of 16  Wed   
39          39 2018-02-24  15:00  Premier League    Matchweek 28  Sat   
40          40 2018-03-03  17:30  Premier League    Matchweek 29  Sat   
41          41 2018-03-06  19:45    Champions Lg     Round of 16  Tue   
42          42 2018-03-10  12:30  Premier League    Matchweek 30  Sat   
43          43 2018-03-17  17:30  Premier League    Matchweek 31  Sat   
44          44 2018-03-31  12:30  Premier League    Matchweek 32  Sat   
45          45 2018-04-04  19:45    Champions Lg  Quarter-finals  Wed   
46          46 2018-04-07  12:30  Premier League    Matchweek 33  Sat   
47          47 2018-04-10  19:45    Champions Lg  Quarter-finals  Tue   
48          48 2018-04-14  17:30  Premier League    Matchweek 34  Sat   
49          49 2018-04-21  12:30  Premier League    Matchweek 35  Sat   
50          50 2018-04-24  19:45    Champions Lg     Semi-finals  Tue   
51          51 2018-04-28  12:30  Premier League    Matchweek 36  Sat   
52          52 2018-05-02  20:45    Champions Lg     Semi-finals  Wed   
53          53 2018-05-06  16:30  Premier League    Matchweek 

In [130]:
get_cum_by_col(df,grouper='Opponent',grouper_name='Opp',cols=['Poss','GA','GF'],agg_func='mean')

Unnamed: 0       Date   Time            Comp           Round  Day  \
0            0 2017-08-12  12:30  Premier League     Matchweek 1  Sat   
1            1 2017-08-15  20:45    Champions Lg  Play-off round  Tue   
2            2 2017-08-19  15:00  Premier League     Matchweek 2  Sat   
3            3 2017-08-23  19:45    Champions Lg  Play-off round  Wed   
4            4 2017-08-27  16:00  Premier League     Matchweek 3  Sun   
5            5 2017-09-09  12:30  Premier League     Matchweek 4  Sat   
6            6 2017-09-13  19:45    Champions Lg     Group stage  Wed   
7            7 2017-09-16  15:00  Premier League     Matchweek 5  Sat   
8            8 2017-09-19  19:45         EFL Cup     Third round  Tue   
9            9 2017-09-23  17:30  Premier League     Matchweek 6  Sat   
10          10 2017-09-26  21:45    Champions Lg     Group stage  Tue   
11          11 2017-10-01  16:30  Premier League     Matchweek 7  Sun   
12          12 2017-10-14  12:30  Premier League     Matchweek 8  Sat   
13          13 2017-10-17  20:45    Champions Lg     Group stage  Tue   
14          14 2017-10-22  16:00  Premier League     Matchweek 9  Sun   
15          15 2017-10-28  15:00  Premier League    Matchweek 10  Sat   
16          16 2017-11-01  19:45    Champions Lg     Group stage  Wed   
17          17 2017-11-04  17:30  Premier League    Matchweek 11  Sat   
18          18 2017-11-18  15:00  Premier League    Matchweek 12  Sat   
19          19 2017-11-21  20:45    Champions Lg     Group stage  Tue   
20          20 2017-11-25  17:30  Premier League    Matchweek 13  Sat   
21          21 2017-11-29  20:00  Premier League    Matchweek 14  Wed   
22          22 2017-12-02  15:00  Premier League    Matchweek 15  Sat   
23          23 2017-12-06  19:45    Champions Lg     Group stage  Wed   
24          24 2017-12-10  14:15  Premier League    Matchweek 16  Sun   
25          25 2017-12-13  20:00  Premier League    Matchweek 17  Wed   
26          26 2017-12-17  16:30  Premier League    Matchweek 18  Sun   
27          27 2017-12-22  19:45  Premier League    Matchweek 19  Fri   
28          28 2017-12-26  17:30  Premier League    Matchweek 20  Tue   
29          29 2017-12-30  15:00  Premier League    Matchweek 21  Sat   
30          30 2018-01-01  15:00  Premier League    Matchweek 22  Mon   
31          31 2018-01-05  19:55          FA Cup     Third round  Fri   
32          32 2018-01-14  16:00  Premier League    Matchweek 23  Sun   
33          33 2018-01-22  20:00  Premier League    Matchweek 24  Mon   
34          34 2018-01-27  19:45          FA Cup    Fourth round  Sat   
35          35 2018-01-30  20:00  Premier League    Matchweek 25  Tue   
36          36 2018-02-04  16:30  Premier League    Matchweek 26  Sun   
37          37 2018-02-11  16:30  Premier League    Matchweek 27  Sun   
38          38 2018-02-14  19:45    Champions Lg     Round of 16  Wed   
39          39 2018-02-24  15:00  Premier League    Matchweek 28  Sat   
40          40 2018-03-03  17:30  Premier League    Matchweek 29  Sat   
41          41 2018-03-06  19:45    Champions Lg     Round of 16  Tue   
42          42 2018-03-10  12:30  Premier League    Matchweek 30  Sat   
43          43 2018-03-17  17:30  Premier League    Matchweek 31  Sat   
44          44 2018-03-31  12:30  Premier League    Matchweek 32  Sat   
45          45 2018-04-04  19:45    Champions Lg  Quarter-finals  Wed   
46          46 2018-04-07  12:30  Premier League    Matchweek 33  Sat   
47          47 2018-04-10  19:45    Champions Lg  Quarter-finals  Tue   
48          48 2018-04-14  17:30  Premier League    Matchweek 34  Sat   
49          49 2018-04-21  12:30  Premier League    Matchweek 35  Sat   
50          50 2018-04-24  19:45    Champions Lg     Semi-finals  Tue   
51          51 2018-04-28  12:30  Premier League    Matchweek 36  Sat   
52          52 2018-05-02  20:45    Champions Lg     Semi-finals  Wed   
53          53 2018-05-06  16:30  Premier League    Matchweek 

In [129]:
#cols = ['GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'] 
gp = df.groupby(['Opponent'])['Win','Draw','Lose']#.index#iloc[12]#.to_dict()
for g,gd in gp:
    print(g)
    print()
    display(gd.shift(1).cumsum())
    print()

Arsenal



Win  Draw  Lose
4   NaN   NaN   NaN
27  1.0   0.0   0.0


Bournemouth



Win  Draw  Lose
26  NaN   NaN   NaN
48  1.0   0.0   0.0


Brighton



...

Win  Draw  Lose
38  NaN   NaN   NaN
41  1.0   0.0   0.0


ru Spartak Moscow



Win  Draw  Lose
10  NaN   NaN   NaN
23  0.0   1.0   0.0


si NK Maribor



Win  Draw  Lose
13  NaN   NaN   NaN
16  1.0   0.0   0.0

In [61]:
pd.DataFrame(df.groupby(['Formation'])['Result','GF','GA'].agg('mean'))

GF        GA
Formation                    
3-4-3      0.000000  5.000000
4-1-4-1    1.600000  1.000000
4-2-3-1    1.892857  1.107143
4-3-2-1    3.000000  0.000000
4-3-3      0.333333  1.333333
4-4-1-1    1.714286  1.000000

In [62]:
#cols = ['GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'] 
gp = df.groupby(['Formation'])['GF','GA',]#.index#iloc[12]#.to_dict()
for g,gd in gp:
    print(g)
    print()
    display(gd.shift(1).expanding().mean())
    print()

3-4-3



GF  GA
3 NaN NaN


4-1-4-1



GF    GA
5        NaN   NaN
9   1.000000  0.00
21  1.500000  1.00
26  2.666667  1.00
27  2.000000  1.25


4-2-3-1



...

GF  GA
6 NaN NaN


4-3-3



GF   GA
34  NaN  NaN
37  1.0  0.0
42  0.5  0.5


4-4-1-1



GF        GA
12       NaN       NaN
13  2.000000  0.000000
14  1.500000  0.000000
15  1.000000  1.333333
16  1.250000  1.000000
18  1.400000  1.400000
19  1.666667  1.166667

In [63]:
#cols = ['GF','GA','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss'] 
gp = df.groupby(['Formation'])['Win','Draw','Lose','Away_Win','Away_Draw','Away_Loss','Home_Win','Home_Draw','Home_Loss']#.index#iloc[12]#.to_dict()
for g,gd in gp:
    print(g)
    print()
    display(gd.shift(1).cumsum())
    print()

3-4-3



Win  Draw  Lose  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  \
3  NaN   NaN   NaN       NaN        NaN        NaN       NaN        NaN   

   Home_Loss  
3        NaN


4-1-4-1



Win  Draw  Lose  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  \
5   NaN   NaN   NaN       NaN        NaN        NaN       NaN        NaN   
9   1.0   0.0   0.0       1.0        0.0        0.0       0.0        0.0   
21  1.0   1.0   0.0       1.0        0.0        0.0       0.0        1.0   
26  2.0   1.0   0.0       1.0        0.0        0.0       1.0        1.0   
27  2.0   1.0   1.0       1.0        0.0        0.0       1.0        1.0   

    Home_Loss  
5         NaN  
9         0.0  
21        0.0  
26        0.0  
27        1.0


4-2-3-1



...

Win  Draw  Lose  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  \
6  NaN   NaN   NaN       NaN        NaN        NaN       NaN        NaN   

   Home_Loss  
6        NaN


4-3-3



Win  Draw  Lose  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  \
34  NaN   NaN   NaN       NaN        NaN        NaN       NaN        NaN   
37  1.0   0.0   0.0       1.0        0.0        0.0       0.0        0.0   
42  1.0   0.0   1.0       1.0        0.0        1.0       0.0        0.0   

    Home_Loss  
34        NaN  
37        0.0  
42        0.0


4-4-1-1



Win  Draw  Lose  Away_Win  Away_Draw  Away_Loss  Home_Win  Home_Draw  \
12  NaN   NaN   NaN       NaN        NaN        NaN       NaN        NaN   
13  1.0   0.0   0.0       1.0        0.0        0.0       0.0        0.0   
14  2.0   0.0   0.0       1.0        0.0        0.0       1.0        0.0   
15  2.0   0.0   1.0       1.0        0.0        1.0       1.0        0.0   
16  3.0   0.0   1.0       1.0        0.0        1.0       2.0        0.0   
18  3.0   0.0   2.0       1.0        0.0        2.0       2.0        0.0   
19  4.0   0.0   2.0       1.0        0.0        2.0       3.0        0.0   

    Home_Loss  
12        NaN  
13        0.0  
14        0.0  
15        0.0  
16        0.0  
18        0.0  
19        0.0

In [87]:
df['Prev_comp'].value_counts()

Premier League    37
Champions Lg      10
EFL Cup            6
FA Cup             6
Super Cup          1
Name: Prev_comp, dtype: int64

In [91]:
df.Captain.value_counts().index[:2]

Index(['César Azpilicueta', 'Jorginho'], dtype='object')

In [ ]:
"""
def duaration6_to_how(row):
    token_hr = int(re.sub('\D','',row.Duration.split(' ')[0]))
    return token_hr
train1.loc[indices_6[1],'Du_hr'] = train1.iloc[indices_6[1]].apply(duaration6_to_how, axis='columns')
"""

OPPPP        Opponent
0       0   es Villarreal
1       0  Crystal Palace
2       0         Arsenal
3       0       Liverpool
4       0     Aston Villa
..    ...             ...
56      1          Wolves
57      1    Leeds United
58      3       Liverpool
59      1  Leicester City
60      1         Watford

[61 rows x 2 columns]

In [86]:
df.OPPPP.value_counts()

0    29
1    24
2     6
3     2
Name: OPPPP, dtype: int64

In [81]:
df.Opponent.value_counts().to_dict()

{'Liverpool': 4,
 'Tottenham': 4,
 'Aston Villa': 3,
 'Southampton': 3,
 'Brentford': 3,
 'Crystal Palace': 3,
 'Burnley': 2,
 'Manchester Utd': 2,
 'fr Lille': 2,
 'Brighton': 2,
 'Wolves': 2,
 'Everton': 2,
 'Leeds United': 2,
 'West Ham': 2,
 'Watford': 2,
 'es Real Madrid': 2,
 'Leicester City': 2,
 'Newcastle Utd': 2,
 'Norwich City': 2,
 'se Malmö': 2,
 'it Juventus': 2,
 'Manchester City': 2,
 'ru Zenit': 2,
 'Arsenal': 2,
 'Chesterfield': 1,
 'Plymouth Argyle': 1,
 'Luton Town': 1,
 'Middlesbrough': 1,
 'es Villarreal': 1}

In [25]:
df.Prev_match_date[0]

NaT

In [26]:
np.nan

nan

In [88]:
df[['Date','Prev_match_date','Rest','Comp','Prev_comp','OPPPP']]

Date Prev_match_date    Rest            Comp       Prev_comp  OPPPP
0  2021-08-11             NaT     NaT       Super Cup             NaN      0
1  2021-08-14      2021-08-11  3 days  Premier League       Super Cup      0
2  2021-08-22      2021-08-14  8 days  Premier League  Premier League      0
3  2021-08-28      2021-08-22  6 days  Premier League  Premier League      0
4  2021-09-11      2021-08-28 14 days  Premier League  Premier League      0
..        ...             ...     ...             ...             ...    ...
56 2022-05-07      2022-05-01  6 days  Premier League  Premier League      1
57 2022-05-11      2022-05-07  4 days  Premier League  Premier League      1
58 2022-05-14      2022-05-11  3 days          FA Cup  Premier League      3
59 2022-05-19      2022-05-14  5 days  Premier League          FA Cup      1
60 2022-05-22      2022-05-19  3 days  Premier League  Premier League      1

[61 rows x 6 columns]

In [21]:
df.Round.values

array(['UEFA Super Cup', 'Matchweek 1', 'Matchweek 2', 'Matchweek 3',
       'Matchweek 4', 'Group stage', 'Matchweek 5', 'Third round',
       'Matchweek 6', 'Group stage', 'Matchweek 7', 'Matchweek 8',
       'Group stage', 'Matchweek 9', 'Fourth round', 'Matchweek 10',
       'Group stage', 'Matchweek 11', 'Matchweek 12', 'Group stage',
       'Matchweek 13', 'Matchweek 14', 'Matchweek 15', 'Group stage',
       'Matchweek 16', 'Matchweek 17', 'Matchweek 18', 'Quarter-finals',
       'Matchweek 19', 'Matchweek 20', 'Matchweek 21', 'Semi-finals',
       'Third round proper', 'Semi-finals', 'Matchweek 22',
       'Matchweek 24', 'Matchweek 23', 'Fourth round proper',
       'Matchweek 26', 'Round of 16', 'Final', 'Fifth round proper',
       'Matchweek 28', 'Matchweek 30', 'Matchweek 29', 'Round of 16',
       'Quarter-finals', 'Matchweek 31', 'Quarter-finals', 'Matchweek 32',
       'Quarter-finals', 'Semi-finals', 'Matchweek 25', 'Matchweek 34',
       'Matchweek 37', 'Matchweek 35'

In [24]:
df.Opponent.value_counts().to_dict()

{'Liverpool': 4,
 'Tottenham': 4,
 'Aston Villa': 3,
 'Southampton': 3,
 'Brentford': 3,
 'Crystal Palace': 3,
 'Burnley': 2,
 'Manchester Utd': 2,
 'fr Lille': 2,
 'Brighton': 2,
 'Wolves': 2,
 'Everton': 2,
 'Leeds United': 2,
 'West Ham': 2,
 'Watford': 2,
 'es Real Madrid': 2,
 'Leicester City': 2,
 'Newcastle Utd': 2,
 'Norwich City': 2,
 'se Malmö': 2,
 'it Juventus': 2,
 'Manchester City': 2,
 'ru Zenit': 2,
 'Arsenal': 2,
 'Chesterfield': 1,
 'Plymouth Argyle': 1,
 'Luton Town': 1,
 'Middlesbrough': 1,
 'es Villarreal': 1}